## Import Libraries & Scripts

In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import scipy.optimize ##scipy optimize
import csv
import time  
import rbfopt ## Blackbox derivative free optimization
from skopt import gp_minimize, forest_minimize ##scikit-optimize
from datetime import datetime
sns.set_style("darkgrid")
sns.set_palette("rainbow")
sns.set_context("talk")

In [2]:
import sys  
sys.path.insert(0, r'C:\Users\kishore.kukreja\Desktop\Inventory Policy Two Echelon\multi-echelon-inventory-optimization\simpy_3.0\simulation')

In [3]:
import os
import math
import random

In [4]:
from simLostSales import simulate_network as lost_sales_simulate
from simBackorder import simulate_network as back_order_simulate

## Read data from Local

In [5]:
# Read the historical demand data
demandAllNodes = []
with open('./simpy_3.0/data/demandData.csv', 'r') as f:
    next(f)  # skip headings
    reader = csv.reader(f)
    for a in reader:
        demandAllNodes.append([float(j) for j in a])

demandAllNodes = np.array(demandAllNodes)  # contains all nodes except the source node

# Read the historical data on lead time delay
leadTimeDelay = []
with open('./simpy_3.0/data/leadTimeExtraDays.csv', 'r') as f:
    reader = csv.reader(f)
    for a in reader:
        leadTimeDelay.append(int(a[0]))

leadTimeDelay = np.array(leadTimeDelay)

In [29]:
leadTimeDelay

array([1, 0, 1, ..., 2, 0, 0])

## Define the Network

In [6]:
numNodes = 6 
nodeNetwork = np.zeros((numNodes, numNodes))
nodeNetwork[0, 1] = 1
nodeNetwork[1, 2] = 1
nodeNetwork[1, 3] = 1
nodeNetwork[3, 4] = 1
nodeNetwork[3, 5] = 1

# Initialize network nodes
defaultLeadTime = np.array([0, 3, 4, 4, 2, 2])
serviceTarget = np.array([0.0, 0.95, 0.95, 0.0, 0.95, 0.95])

In [7]:
nodeNetwork

array([[0., 1., 0., 0., 0., 0.],
       [0., 0., 1., 1., 0., 0.],
       [0., 0., 0., 0., 0., 0.],
       [0., 0., 0., 0., 1., 1.],
       [0., 0., 0., 0., 0., 0.],
       [0., 0., 0., 0., 0., 0.]])

## Scipy Optimize Nelder-Mead

In [8]:
# function to evaluate the objective function for optimization
# we minimize on-hand inventory and heavily penalize not meeting
# the beta service level (demand volume based)

### Nelder-Mead Define Function

In [10]:
def getObj_NMScipy(initial_guess, args):

    demandAllNodes,\
    leadTimeDelay,\
    numNodes,\
    nodeNetwork,\
    defaultLeadTime,\
    event_simulation,\
    serviceTarget = args['dd'],args['lt'],args['n'],args['net'],args['dlt'],args['event_simulation'],args['sl']

    # Split the initial guess to get base stock and ROP
    excess_inventory_guess = initial_guess[:(numNodes - 1)]
    ROP_guess = initial_guess[(numNodes - 1):]
    base_stock_guess = np.add(excess_inventory_guess, ROP_guess)
    
    # Insert the supply node's base stock
    baseStock = np.insert(base_stock_guess, 0, 10000)
    
    # Insert a zero ROP for the first source node
    ROP = np.insert(ROP_guess, 0, 0)
    
    # Initialize inventory level
    initialInv = 0.9*baseStock
    
    replications = 20
    totServiceLevel = np.zeros(numNodes)
    totAvgOnHand = 0.0
    if event_simulation=='Lost Sales':
        for i in range(replications):
            print('------------------------------Back Order Simulation------------------------------------------')
            nodes = back_order_simulate(i,numNodes,nodeNetwork,initialInv,ROP,baseStock,
                                     demandAllNodes,defaultLeadTime,leadTimeDelay)

            totServiceLevel = np.array([totServiceLevel[j] + 
                                        nodes[j].serviceLevel for j in range(len(nodes))]) #convert list to array
            print('------------------------------Total Service Level------------------------------------------')
            print(totServiceLevel)
            totAvgOnHand += np.sum([nodes[j].avgOnHand for j in range(len(nodes))])
            print('------------------------------Total Average on Hand------------------------------------------')
            print('Per Node On hand:',[nodes[j].avgOnHand for j in range(len(nodes))])
            print('Total On hand:',totAvgOnHand)
        servLevelPenalty = np.maximum(0, serviceTarget - totServiceLevel/replications) # element-wise max
        print('Service level penalty:',servLevelPenalty)
        objFunValue = totAvgOnHand/replications + 1.0e6*np.sum(servLevelPenalty)
        print('Objective Function value:',objFunValue)
    elif event_simulation=='Back Order':
        for i in range(replications):
            print('------------------------------Back Order Simulation------------------------------------------')
            nodes = back_order_simulate(i,numNodes,nodeNetwork,initialInv,ROP,baseStock,
                                     demandAllNodes,defaultLeadTime,leadTimeDelay)

            totServiceLevel = np.array([totServiceLevel[j] + 
                                        nodes[j].serviceLevel for j in range(len(nodes))]) #convert list to array
            print('------------------------------Total Service Level------------------------------------------')
            print(totServiceLevel)
            totAvgOnHand += np.sum([nodes[j].avgOnHand for j in range(len(nodes))])
            print('------------------------------Total Average on Hand------------------------------------------')
            print('Per Node On hand:',[nodes[j].avgOnHand for j in range(len(nodes))])
            print('Total On hand:',totAvgOnHand)
        servLevelPenalty = np.maximum(0, serviceTarget - totServiceLevel/replications) # element-wise max
        print('Service level penalty:',servLevelPenalty)
        objFunValue = totAvgOnHand/replications + 1.0e6*np.sum(servLevelPenalty)
        print('Objective Function value:',objFunValue)
    return objFunValue

In [11]:
# Callback function to print optimization iterations
niter = 1
def callbackF(xk):
    global niter
    print('{0:4d}    {1:6.6f}'.format(niter, getObj_NMScipy(xk, allData)))
    niter += 1

### Nelder-Mead Control parameters

In [13]:
######## Main statements to call optimization ########
######## For Finding Optimum Values Equivalent to training ###########
excess_inventory_initial_guess = [2000, 350, 700, 150, 400]
ROP_initial_guess = [1000, 250, 200, 150, 200]
guess = excess_inventory_initial_guess + ROP_initial_guess # concatenate lists

NUM_CYCLES = 5 # 100
TIME_LIMIT = 10 # 1440 minutes
start_time = time.time()
print("\nMax time limit: " + str(TIME_LIMIT) + " minutes")
print("Max algorithm cycles: " + str(NUM_CYCLES) + " (50 iterations per cycle)")
print("The algorithm will run either for " + str(TIME_LIMIT) + " minutes or " + str(NUM_CYCLES) + " cycles")


Max time limit: 10 minutes
Max algorithm cycles: 5 (50 iterations per cycle)
The algorithm will run either for 10 minutes or 5 cycles


### Nelder-Mead Lost Sales Optimization

In [14]:
event_simulation='Lost Sales'
# Combine all datasets
allData = {'dd':   demandAllNodes,\
            'lt':  leadTimeDelay,\
            'n':   numNodes,\
            'net': nodeNetwork,\
            'dlt': defaultLeadTime,\
            'event_simulation':event_simulation,\
            'sl':  serviceTarget
        }

In [15]:
ctr = 1
elapsed_time = (time.time() - start_time)/60.0
while ctr <= NUM_CYCLES and elapsed_time <= TIME_LIMIT:
    print('\nCycle: ' + str(ctr))
    print('{0:4s}    {1:9s}'.format('Iter', 'Obj'))
    optROP = scipy.optimize.minimize(fun=getObj_NMScipy
    							, x0=guess
    							, args=allData
    							, method='Nelder-Mead'
    							, callback=callbackF
    							, options={'disp': True,'maxiter':5})
    #'maxiter':5 # 50 change later
    guess = optROP.x
    ctr += 1
    elapsed_time = (time.time() - start_time)/60.0


Cycle: 1
Iter    Obj      
------------------------------Back Order Simulation------------------------------------------
------------------------------Total Service Level------------------------------------------
[1.         0.96601387 1.         1.         1.         0.96799848]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 1550.566399891239, 318.18280167008277, 440.1902991582252, 191.28361772815296, 266.2487353024479]
Total On hand: 2766.4718537501476
------------------------------Back Order Simulation------------------------------------------
------------------------------Total Service Level------------------------------------------
[2.         1.95525705 1.99982844 2.         1.99741324 1.91904193]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 1540.72463754859, 282.19650574358644, 403.74785566748875, 178.97825591557836, 265.26769809103746]

Per Node On hand: [0.0, 1561.8469044164194, 290.52285627866144, 406.6434289503752, 179.7261622182154, 271.68573896291485]
Total On hand: 52537.52625150082
------------------------------Back Order Simulation------------------------------------------
------------------------------Total Service Level------------------------------------------
[20.         19.60851373 19.94276585 20.         19.99423507 19.33692359]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 1594.4308698250327, 311.659538055735, 449.21025941240754, 184.61768706863876, 275.2547866772422]
Total On hand: 55352.69939253988
Service level penalty: [0. 0. 0. 0. 0. 0.]
Objective Function value: 2767.634969626994
------------------------------Back Order Simulation------------------------------------------
------------------------------Total Service Level------------------------------------------
[1.         0.99784295 1.         1.         1.         0.990201

------------------------------Total Service Level------------------------------------------
[16.         15.69370418 15.95338248 16.         15.97877977 15.51102111]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 1652.1600932207994, 324.4736124621898, 452.03660015434144, 185.52907400935905, 281.54289102769917]
Total On hand: 45053.711841950186
------------------------------Back Order Simulation------------------------------------------
------------------------------Total Service Level------------------------------------------
[17.         16.67417119 16.95338248 17.         16.97877977 16.47394869]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 1622.1821400197473, 312.5695326115833, 417.3306382108609, 182.70415159449507, 262.731491248826]
Total On hand: 47851.2297956357
------------------------------Back Order Simulation--------------------------

------------------------------Total Service Level------------------------------------------
[13.         12.65520858 12.9381759  13.         12.97735354 12.58213648]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 1566.15722904733, 307.4574840795855, 491.8266270138367, 188.69893079027995, 295.71767980417894]
Total On hand: 35783.56374788468
------------------------------Back Order Simulation------------------------------------------
------------------------------Total Service Level------------------------------------------
[14.         13.64063507 13.92963696 14.         13.97735354 13.56464848]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 1506.9518360620216, 290.2587470353084, 425.4329832303148, 178.73638159567722, 276.3425283823329]
Total On hand: 38461.286224190335
------------------------------Back Order Simulation---------------------------

------------------------------Total Service Level------------------------------------------
[10.          9.81887648  9.97690426 10.          9.98468149  9.685777  ]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 1579.1754601081002, 298.9981953833005, 470.0907674889717, 185.9396488863759, 294.5307130736123]
Total On hand: 27811.120700707197
------------------------------Back Order Simulation------------------------------------------
------------------------------Total Service Level------------------------------------------
[11.         10.78982298 10.97548899 11.         10.98468149 10.63441453]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 1478.159998890168, 305.4068672013575, 425.8373815455649, 186.28811048110566, 252.85050406144234]
Total On hand: 30459.663562886835
------------------------------Back Order Simulation--------------------------

...

------------------------------Total Service Level------------------------------------------
[15.         14.38428914 14.95484062 15.         15.         14.51820599]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 1308.423873480647, 300.51681316050195, 456.0797904372362, 200.38929601124312, 297.99794262806034]
Total On hand: 39114.1231690309
------------------------------Back Order Simulation------------------------------------------
------------------------------Total Service Level------------------------------------------
[16.         15.32022599 15.95478783 16.         16.         15.46823354]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 1373.5532478437249, 314.0680318861566, 404.41503461324527, 196.2296121817118, 266.3842867638669]
Total On hand: 41668.7733823196
------------------------------Back Order Simulation----------------------------

------------------------------Total Service Level------------------------------------------
[13.         12.50405095 12.98167646 13.         13.         12.49117306]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 1303.402213046189, 337.18253823087895, 412.2484483027289, 199.09689212587074, 264.4576396800941]
Total On hand: 34172.38642064048
------------------------------Back Order Simulation------------------------------------------
------------------------------Total Service Level------------------------------------------
[14.         13.46524909 13.96633729 14.         14.         13.46020487]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 1302.4258080501943, 300.37000719732185, 407.3547176959483, 191.4571445950382, 301.9562574739833]
Total On hand: 36675.95035565297
------------------------------Back Order Simulation---------------------------

------------------------------Total Service Level------------------------------------------
[10.          9.60746919  9.96999109 10.         10.          9.64662053]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 1508.5456959254411, 299.32501704018665, 411.5765261809718, 190.39595057267474, 281.74197754177675]
Total On hand: 26166.315855998648
------------------------------Back Order Simulation------------------------------------------
------------------------------Total Service Level------------------------------------------
[11.         10.55441415 10.9646538  11.         11.         10.62623979]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 1357.1365332322628, 311.356210230802, 397.6359777166866, 191.38279030746497, 289.3625108856291]
Total On hand: 28713.189878371493
------------------------------Back Order Simulation------------------------

------------------------------Back Order Simulation------------------------------------------
------------------------------Total Service Level------------------------------------------
[7.         6.69078018 6.96633614 7.         6.99956748 6.80191487]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 1486.4764756071465, 332.834964581822, 479.1224065053153, 200.23728627598499, 285.955854744566]
Total On hand: 18520.141198622547
------------------------------Back Order Simulation------------------------------------------
------------------------------Total Service Level------------------------------------------
[8.         7.62439491 7.96312806 8.         7.99956748 7.73708072]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 1460.1147703145928, 314.9232018636073, 434.82977577422355, 191.0158933094274, 274.39517353430176]
Total On hand: 21195.42001341

------------------------------Total Service Level------------------------------------------
[3.         2.8684799  3.         3.         3.         2.92747614]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 1372.519516389346, 314.3725345229359, 404.6108765621296, 190.8220842176394, 273.34180002491615]
Total On hand: 7868.645426445213
------------------------------Back Order Simulation------------------------------------------
------------------------------Total Service Level------------------------------------------
[4.         3.84377944 3.99672909 4.         4.         3.85872435]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 1318.7837804402177, 314.374369179088, 419.9345699378349, 199.90350972096323, 270.1568125471908]
Total On hand: 10391.798468270508
------------------------------Back Order Simulation----------------------------------------

In [16]:
print("\nFinal optimized objective: " + "{0:10.3f}".format(getObj_NMScipy(optROP.x, allData)))
print("\nFinal optimized solution: " + str(optROP.x))
print("\nTotal time: " + "{0:3.2f}".format(elapsed_time) + " minutes")

------------------------------Back Order Simulation------------------------------------------
------------------------------Total Service Level------------------------------------------
[1.         0.93999461 1.         1.         1.         0.96705269]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 1414.481756124586, 319.75365997841243, 438.46002172008514, 196.985312931875, 301.6214240510222]
Total On hand: 2671.3021748059805
------------------------------Back Order Simulation------------------------------------------
------------------------------Total Service Level------------------------------------------
[2.         1.88788002 2.         2.         2.         1.95676204]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 1351.2420871070283, 309.76042029896684, 471.7317002991161, 194.7914443399397, 314.1507878772157]
Total On hand: 5312.978614728

------------------------------Total Service Level------------------------------------------
[20.         19.13922752 19.94627901 20.         19.99399617 19.34223033]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 1334.6896059312799, 308.2231546959908, 458.9352420340007, 188.51952994175926, 314.02177617640695]
Total On hand: 52065.610942985004
Service level penalty: [0. 0. 0. 0. 0. 0.]
Objective Function value: 2603.28054714925

Final optimized objective:   2603.281

Final optimized solution: [1999.55      361.6445    723.289     162.740025  413.308     812.7
  258.3175    206.654     154.9905    206.654   ]

Total time: 2.31 minutes


In [17]:
final_solution=optROP.x

In [18]:
final_inventory_stock = final_solution[:(numNodes - 1)]
final_ROP = final_solution[(numNodes - 1):]
print('Optimized Inventory Position',np.round(final_inventory_stock)) ## [ plant_area WH1  WH2 Store1 Store2]
print('Optimized Reoorder point',np.round(final_ROP))                 ## [ plant_area WH1  WH2 Store1 Store2]

Optimized Inventory Position [2000.  362.  723.  163.  413.]
Optimized Reoorder point [813. 258. 207. 155. 207.]


### Predict Nelder-Mead Lost Sales Using Inputs and Optimized values

In [34]:
#New demand = Number of replications rows * (nodes -1) columns 
#New lead time= Number of replications rows * one column 
replications = 20 
demand_input=np.random.randint(1,100,(replications,numNodes-1))
leadtime_input=np.random.randint(1,5,replications)

In [31]:
event_simulation='Lost Sales'
# Combine all datasets
allData = {'dd':   demand_input,\
            'lt':  leadtime_input,\
            'n':   numNodes,\
            'net': nodeNetwork,\
            'dlt': defaultLeadTime,\
            'event_simulation':event_simulation,\
            'sl':  serviceTarget
        }

In [33]:
print("\nFinal predicted objective: " + "{0:10.3f}".format(getObj_NMScipy(optROP.x, allData)))
print("\nFinal predicted solution: " + str(optROP.x))

------------------------------Back Order Simulation------------------------------------------
------------------------------Total Service Level------------------------------------------
[1.         0.7542659  0.54489538 0.07158092 0.0977535  0.13300745]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 703.2893472430546, 72.89399166666655, 16.266490243055564, 4.2579204305555525, 19.03606]
Total On hand: 815.7438095833324
------------------------------Back Order Simulation------------------------------------------
------------------------------Total Service Level------------------------------------------
[2.         1.50188834 0.97166683 0.14595961 0.19988691 0.22743024]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 659.3818884097215, 58.320237222222104, 16.274531611111126, 4.016884173611108, 8.487843888888891]
Total On hand: 1562.225194888887
-----

------------------------------Total Service Level------------------------------------------
[18.         13.64276439  8.22315322  1.38250553  1.78426373  1.82227949]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 653.4729304999992, 52.83067111111101, 12.349624256944455, 3.0461789097222183, 8.074050000000002]
Total On hand: 13822.884712465262
------------------------------Back Order Simulation------------------------------------------
------------------------------Total Service Level------------------------------------------
[19.         14.32275235  8.73172858  1.4824637   1.8886388   1.95028565]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 704.7692539652769, 66.34319833333322, 13.663563000000012, 4.042770722222219, 13.877378333333334]
Total On hand: 14625.580876819427
------------------------------Back Order Simulation-------------------------

### Nelder-Mead Back Order Optimization

In [39]:
event_simulation='Back Order'
# Combine all datasets
allData = {'dd':   demandAllNodes,\
            'lt':  leadTimeDelay,\
            'n':   numNodes,\
            'net': nodeNetwork,\
            'dlt': defaultLeadTime,\
            'event_simulation':event_simulation,\
            'sl':  serviceTarget
        }

In [40]:
ctr = 1
start_time=time.time()
elapsed_time = (time.time() - start_time)/60.0
while ctr <= NUM_CYCLES and elapsed_time <= TIME_LIMIT:
    print('\nCycle: ' + str(ctr))
    print('{0:4s}    {1:9s}'.format('Iter', 'Obj'))
    optROP = scipy.optimize.minimize(fun=getObj_NMScipy
    							, x0=guess
    							, args=allData
    							, method='Nelder-Mead'
    							, callback=callbackF
    							, options={'disp': True,'maxiter':5})
    #'maxiter':5 # 50 change later
    guess = optROP.x
    ctr += 1
    elapsed_time = (time.time() - start_time)/60.0

print("\nFinal objective: " + "{0:10.3f}".format(getObj_NMScipy(optROP.x, allData)))
print("\nFinal solution: " + str(optROP.x))
print("\nTotal time: " + "{0:3.2f}".format(elapsed_time) + " minutes")


Cycle: 1
Iter    Obj      
------------------------------Back Order Simulation------------------------------------------
------------------------------Total Service Level------------------------------------------
[1.         0.93999461 1.         1.         1.         0.96705269]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 1414.481756124586, 319.75365997841243, 438.46002172008514, 196.985312931875, 301.6214240510222]
Total On hand: 2671.3021748059805
------------------------------Back Order Simulation------------------------------------------
------------------------------Total Service Level------------------------------------------
[2.         1.88788002 2.         2.         2.         1.95676204]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 1351.2420871070283, 309.76042029896684, 471.7317002991161, 194.7914443399397, 314.1507878772157]
T

------------------------------Total Service Level------------------------------------------
[20.         19.13922752 19.94627901 20.         19.99399617 19.34223033]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 1334.6896059312799, 308.2231546959908, 458.9352420340007, 188.51952994175926, 314.02177617640695]
Total On hand: 52065.610942985004
Service level penalty: [0. 0. 0. 0. 0. 0.]
Objective Function value: 2603.28054714925
------------------------------Back Order Simulation------------------------------------------
------------------------------Total Service Level------------------------------------------
[1.         0.95445754 1.         1.         1.         0.97722146]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 1501.0822407144567, 323.22387067651175, 441.8542548262742, 193.81286856167839, 294.18053946922834]
Total On hand: 2754.1537742

------------------------------Total Service Level------------------------------------------
[20.         19.09389508 19.97451655 20.         19.93616573 19.40858605]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 1469.8422320948678, 311.83724349242186, 435.6141939832866, 183.44977625655713, 297.8982908180003]
Total On hand: 53618.50200891644
Service level penalty: [0. 0. 0. 0. 0. 0.]
Objective Function value: 2680.925100445822
------------------------------Back Order Simulation------------------------------------------
------------------------------Total Service Level------------------------------------------
[1.         0.96845985 1.         1.         1.         0.98979058]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 1467.2497014113837, 330.03295409653583, 455.55100254200715, 201.549563564509, 298.1199961429554]
Total On hand: 2752.503217757

------------------------------Total Service Level------------------------------------------
[19.         18.10808106 18.95831025 19.         18.97431934 18.31241284]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 1488.433071964725, 321.5512107846623, 470.3685794320774, 195.96996963429783, 303.23928197581523]
Total On hand: 49924.669809717016
------------------------------Back Order Simulation------------------------------------------
------------------------------Total Service Level------------------------------------------
[20.         19.06226067 19.95831025 20.         19.9545895  19.21112062]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 1413.6999920351063, 330.75659310196846, 418.5043541186835, 194.13150919255253, 258.74341920792]
Total On hand: 52540.50567737325
Service level penalty: [0. 0. 0. 0. 0. 0.]
Objective Function value: 2627.0252

------------------------------Total Service Level------------------------------------------
[20.         19.04939037 19.90894654 20.         19.99306391 19.25283822]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 1414.1575349544205, 325.3755849068634, 463.7470458162347, 199.12396084260254, 313.1179591799652]
Total On hand: 52620.12020911325
Service level penalty: [0. 0. 0. 0. 0. 0.]
Objective Function value: 2631.0060104556624
------------------------------Back Order Simulation------------------------------------------
------------------------------Total Service Level------------------------------------------
[1.         0.97747168 1.         1.         1.         0.98556117]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 1519.0623880071294, 323.5934184732264, 446.3035701039881, 202.0482907975959, 289.5912913304875]
Total On hand: 2780.5989587124

...

------------------------------Total Service Level------------------------------------------
[3.         2.8684799  3.         3.         3.         2.92747614]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 1372.519516389346, 314.3725345229359, 404.6108765621296, 190.8220842176394, 273.34180002491615]
Total On hand: 7868.645426445213
------------------------------Back Order Simulation------------------------------------------
------------------------------Total Service Level------------------------------------------
[4.         3.84377944 3.99672909 4.         4.         3.85872435]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 1318.7837804402177, 314.374369179088, 419.9345699378349, 199.90350972096323, 270.1568125471908]
Total On hand: 10391.798468270508
------------------------------Back Order Simulation----------------------------------------

------------------------------Total Service Level------------------------------------------
[3.         2.87068001 2.99696609 3.         2.99956748 2.89348966]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 1422.4801939724716, 324.42769816681505, 416.006999674323, 196.7059418781064, 258.03848133230537]
Total On hand: 7924.66599475901
------------------------------Back Order Simulation------------------------------------------
------------------------------Total Service Level------------------------------------------
[4.         3.83981877 3.99696609 4.         3.99956748 3.87835999]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 1403.0832312522596, 328.4198937551965, 492.02166983000836, 193.98459888422363, 298.27294651538466]
Total On hand: 10640.448334996083
------------------------------Back Order Simulation-------------------------------------

------------------------------Total Service Level------------------------------------------
[20.         19.15103854 19.89756082 20.         19.99118999 19.24878925]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 1424.0213364683011, 314.90802725578556, 446.49827250585656, 193.81011015219258, 289.69629211316555]
Total On hand: 52737.50290637339
Service level penalty: [0. 0. 0. 0. 0. 0.]
Objective Function value: 2636.8751453186696
------------------------------Back Order Simulation------------------------------------------
------------------------------Total Service Level------------------------------------------
[1.         0.93999461 1.         1.         1.         0.96705269]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 1414.481756124586, 319.75365997841243, 438.46002172008514, 196.985312931875, 301.6214240510222]
Total On hand: 2671.3021748

------------------------------Total Service Level------------------------------------------
[18.         17.22632621 17.9492411  18.         17.99780311 17.38542937]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 1373.0716905139375, 303.3516016099228, 397.64953535396796, 194.9760690138199, 266.0293072182291]
Total On hand: 46853.37418841888
------------------------------Back Order Simulation------------------------------------------
------------------------------Total Service Level------------------------------------------
[19.         18.16342967 18.94627901 19.         18.99399617 18.34593671]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 1375.4430434309722, 306.0115931907368, 436.82742559580254, 184.68437029557916, 304.8810132736017]
Total On hand: 49461.22163420557
------------------------------Back Order Simulation--------------------------

------------------------------Total Service Level------------------------------------------
[15.         14.38428914 14.95484062 15.         15.         14.51820599]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 1308.423873480647, 300.51681316050195, 456.0797904372362, 200.38929601124312, 297.99794262806034]
Total On hand: 39114.1231690309
------------------------------Back Order Simulation------------------------------------------
------------------------------Total Service Level------------------------------------------
[16.         15.32022599 15.95478783 16.         16.         15.46823354]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 1373.5532478437249, 314.0680318861566, 404.41503461324527, 196.2296121817118, 266.3842867638669]
Total On hand: 41668.7733823196
------------------------------Back Order Simulation----------------------------

In [41]:
print("\nFinal objective: " + "{0:10.3f}".format(getObj_NMScipy(optROP.x, allData)))
print("\nFinal solution: " + str(optROP.x))
print("\nTotal time: " + "{0:3.2f}".format(elapsed_time) + " minutes")

------------------------------Back Order Simulation------------------------------------------
------------------------------Total Service Level------------------------------------------
[1.         0.93999461 1.         1.         1.         0.96705269]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 1414.481756124586, 319.75365997841243, 438.46002172008514, 196.985312931875, 301.6214240510222]
Total On hand: 2671.3021748059805
------------------------------Back Order Simulation------------------------------------------
------------------------------Total Service Level------------------------------------------
[2.         1.88788002 2.         2.         2.         1.95676204]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 1351.2420871070283, 309.76042029896684, 471.7317002991161, 194.7914443399397, 314.1507878772157]
Total On hand: 5312.978614728

------------------------------Total Service Level------------------------------------------
[19.         18.16342967 18.94627901 19.         18.99399617 18.34593671]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 1375.4430434309722, 306.0115931907368, 436.82742559580254, 184.68437029557916, 304.8810132736017]
Total On hand: 49461.22163420557
------------------------------Back Order Simulation------------------------------------------
------------------------------Total Service Level------------------------------------------
[20.         19.13922752 19.94627901 20.         19.99399617 19.34223033]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 1334.6896059312799, 308.2231546959908, 458.9352420340007, 188.51952994175926, 314.02177617640695]
Total On hand: 52065.610942985004
Service level penalty: [0. 0. 0. 0. 0. 0.]
Objective Function value: 2603.2

In [42]:
final_solution=optROP.x

In [43]:
final_inventory_stock = final_solution[:(numNodes - 1)]
final_ROP = final_solution[(numNodes - 1):]
print('Optimized Inventory Position',np.round(final_inventory_stock)) ## [ plant_area WH1  WH2 Store1 Store2]
print('Optimized Reoorder point',np.round(final_ROP))                 ## [ plant_area WH1  WH2 Store1 Store2]

Optimized Inventory Position [2000.  362.  723.  163.  413.]
Optimized Reoorder point [813. 258. 207. 155. 207.]


### Predict Nelder-Mead Back Order Using Inputs and Optimized values

In [44]:
#New demand = Number of replications rows * (nodes -1) columns 
#New lead time= Number of replications rows * one column 
replications = 20 
demand_input=np.random.randint(1,100,(replications,numNodes-1))
leadtime_input=np.random.randint(1,5,replications)

In [45]:
event_simulation='Lost Sales'
# Combine all datasets
allData = {'dd':   demand_input,\
            'lt':  leadtime_input,\
            'n':   numNodes,\
            'net': nodeNetwork,\
            'dlt': defaultLeadTime,\
            'event_simulation':event_simulation,\
            'sl':  serviceTarget
        }

In [46]:
print("\nFinal predicted objective: " + "{0:10.3f}".format(getObj_NMScipy(optROP.x, allData)))
print("\nFinal predicted solution: " + str(optROP.x))

------------------------------Back Order Simulation------------------------------------------
------------------------------Total Service Level------------------------------------------
[1.         0.74993405 0.47188917 0.06694124 0.11079241 0.08232611]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 734.9149395208326, 59.75248166666657, 12.432823743055563, 5.5692092986111055, 7.457478333333334]
Total On hand: 820.1269325624992
------------------------------Back Order Simulation------------------------------------------
------------------------------Total Service Level------------------------------------------
[2.         1.48630078 0.9828207  0.1435596  0.19353851 0.16107899]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 697.5327220347214, 69.80624277777765, 16.711769694444452, 3.936446749999997, 10.184971111111112]
Total On hand: 1618.299084930

------------------------------Total Service Level------------------------------------------
[19.         13.81740466  9.20474029  1.4269054   1.82131885  1.67771027]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 728.9010992569436, 74.52149499999987, 14.478278027777792, 4.041667784722217, 10.920459444444447]
Total On hand: 15356.911403840257
------------------------------Back Order Simulation------------------------------------------
------------------------------Total Service Level------------------------------------------
[20.         14.54608003  9.62403077  1.48898564  1.91488008  1.7858465 ]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 714.0303009930545, 51.21092055555546, 15.81483775000001, 4.188594118055552, 11.531253888888891]
Total On hand: 16153.687311145812
Service level penalty: [0.         0.222696   0.46879846 0.         0.854256 

### Insights

Back POrder
Optimized Inventory Position [2000.  362.  723.  163.  413.]
Optimized Reoorder point [813. 258. 207. 155. 207.]

## Scikit Optimize GP Minimize

### GP Minimize Define Function

In [47]:
def getObj_GP_minimize_lost_sales(initial_guess):

    # Split the initial guess to get base stock and ROP
    excess_inventory_guess = initial_guess[:(numNodes - 1)]
    ROP_guess = initial_guess[(numNodes - 1):]
    base_stock_guess = np.add(excess_inventory_guess, ROP_guess)
    
    # Insert the supply node's base stock
    baseStock = np.insert(base_stock_guess, 0, 10000)
    
    # Insert a zero ROP for the first source node
    ROP = np.insert(ROP_guess, 0, 0)
    
    # Initialize inventory level
    initialInv = 0.9*baseStock
    
    replications = 20
    totServiceLevel = np.zeros(numNodes)
    totAvgOnHand = 0.0
    for i in range(replications):
        nodes = lost_sales_simulate(i,numNodes,nodeNetwork,initialInv,ROP,baseStock,\
                                 demandAllNodes,defaultLeadTime,leadTimeDelay)
        print('------------------------------Total Service Level------------------------------------------')
        totServiceLevel = np.array([totServiceLevel[j] + \
                                    nodes[j].serviceLevel for j in range(len(nodes))]) #convert list to array
        print(totServiceLevel)
        totAvgOnHand += np.sum([nodes[j].avgOnHand for j in range(len(nodes))])
        print('------------------------------Total Average on Hand------------------------------------------')
        print('Per Node On hand:',[nodes[j].avgOnHand for j in range(len(nodes))])
        print('Total On hand:',totAvgOnHand)
    servLevelPenalty = np.maximum(0, serviceTarget - totServiceLevel/replications) # element-wise max
    print('Service level penalty:',servLevelPenalty)
    objFunValue = totAvgOnHand/replications + 1.0e6*np.sum(servLevelPenalty)
    print('Objective Function value:',objFunValue)
    return objFunValue

In [48]:
def getObj_GP_minimize_back_order(initial_guess):

    # Split the initial guess to get base stock and ROP
    excess_inventory_guess = initial_guess[:(numNodes - 1)]
    ROP_guess = initial_guess[(numNodes - 1):]
    base_stock_guess = np.add(excess_inventory_guess, ROP_guess)
    
    # Insert the supply node's base stock
    baseStock = np.insert(base_stock_guess, 0, 10000)
    
    # Insert a zero ROP for the first source node
    ROP = np.insert(ROP_guess, 0, 0)
    
    # Initialize inventory level
    initialInv = 0.9*baseStock
    
    replications = 20
    totServiceLevel = np.zeros(numNodes)
    totAvgOnHand = 0.0
    for i in range(replications):
        nodes = back_order_simulate(i,numNodes,nodeNetwork,initialInv,ROP,baseStock,\
                                 demandAllNodes,defaultLeadTime,leadTimeDelay)
        print('------------------------------Total Service Level------------------------------------------')
        totServiceLevel = np.array([totServiceLevel[j] + \
                                    nodes[j].serviceLevel for j in range(len(nodes))]) #convert list to array
        print(totServiceLevel)
        totAvgOnHand += np.sum([nodes[j].avgOnHand for j in range(len(nodes))])
        print('------------------------------Total Average on Hand------------------------------------------')
        print('Per Node On hand:',[nodes[j].avgOnHand for j in range(len(nodes))])
        print('Total On hand:',totAvgOnHand)
    servLevelPenalty = np.maximum(0, serviceTarget - totServiceLevel/replications) # element-wise max
    print('Service level penalty:',servLevelPenalty)
    objFunValue = totAvgOnHand/replications + 1.0e6*np.sum(servLevelPenalty)
    print('Objective Function value:',objFunValue)
    return objFunValue

In [74]:
def predict_GP_minimize_lost_sales(initial_guess):

    # Split the initial guess to get base stock and ROP
    excess_inventory_guess = initial_guess[:(numNodes - 1)]
    ROP_guess = initial_guess[(numNodes - 1):]
    base_stock_guess = np.add(excess_inventory_guess, ROP_guess)
    
    # Insert the supply node's base stock
    baseStock = np.insert(base_stock_guess, 0, 10000)
    
    # Insert a zero ROP for the first source node
    ROP = np.insert(ROP_guess, 0, 0)
    
    # Initialize inventory level
    initialInv = 0.9*baseStock
    
    replications = 20
    totServiceLevel = np.zeros(numNodes)
    totAvgOnHand = 0.0
    
    
    demand_input=np.random.randint(1,100,(replications,numNodes-1))
    leadtime_input=np.random.randint(1,5,replications)
    
    
    for i in range(replications):
        nodes = lost_sales_simulate(i,numNodes,nodeNetwork,initialInv,ROP,baseStock,\
                                 demand_input,defaultLeadTime,leadtime_input)
        print('------------------------------Total Service Level------------------------------------------')
        totServiceLevel = np.array([totServiceLevel[j] + \
                                    nodes[j].serviceLevel for j in range(len(nodes))]) #convert list to array
        print(totServiceLevel)
        totAvgOnHand += np.sum([nodes[j].avgOnHand for j in range(len(nodes))])
        print('------------------------------Total Average on Hand------------------------------------------')
        print('Per Node On hand:',[nodes[j].avgOnHand for j in range(len(nodes))])
        print('Total On hand:',totAvgOnHand)
    servLevelPenalty = np.maximum(0, serviceTarget - totServiceLevel/replications) # element-wise max
    print('Service level penalty:',servLevelPenalty)
    objFunValue = totAvgOnHand/replications + 1.0e6*np.sum(servLevelPenalty)
    print('Objective Function value:',objFunValue)
    return objFunValue

In [84]:
def predict_GP_minimize_back_order(initial_guess):

    # Split the initial guess to get base stock and ROP
    excess_inventory_guess = initial_guess[:(numNodes - 1)]
    ROP_guess = initial_guess[(numNodes - 1):]
    base_stock_guess = np.add(excess_inventory_guess, ROP_guess)
    
    # Insert the supply node's base stock
    baseStock = np.insert(base_stock_guess, 0, 10000)
    
    # Insert a zero ROP for the first source node
    ROP = np.insert(ROP_guess, 0, 0)
    
    # Initialize inventory level
    initialInv = 0.9*baseStock
    
    
    
    replications = 20
    
    demand_input=np.random.randint(1,100,(replications,numNodes-1))
    leadtime_input=np.random.randint(1,5,replications)
    
    totServiceLevel = np.zeros(numNodes)
    totAvgOnHand = 0.0
    for i in range(replications):
        nodes = back_order_simulate(i,numNodes,nodeNetwork,initialInv,ROP,baseStock,\
                                 demand_input,defaultLeadTime,leadtime_input)
        print('------------------------------Total Service Level------------------------------------------')
        totServiceLevel = np.array([totServiceLevel[j] + \
                                    nodes[j].serviceLevel for j in range(len(nodes))]) #convert list to array
        print(totServiceLevel)
        totAvgOnHand += np.sum([nodes[j].avgOnHand for j in range(len(nodes))])
        print('------------------------------Total Average on Hand------------------------------------------')
        print('Per Node On hand:',[nodes[j].avgOnHand for j in range(len(nodes))])
        print('Total On hand:',totAvgOnHand)
    servLevelPenalty = np.maximum(0, serviceTarget - totServiceLevel/replications) # element-wise max
    print('Service level penalty:',servLevelPenalty)
    objFunValue = totAvgOnHand/replications + 1.0e6*np.sum(servLevelPenalty)
    print('Objective Function value:',objFunValue)
    return objFunValue

In [75]:
# Callback function to print optimization iterations
niter = 1
def callbackF(res):
    global niter
    print('{0:4d}    {1:6.6f}'.format(niter, res.fun))
    niter += 1

### GP Minimize Control Parameters

In [50]:
######## Main statements to call optimization ########
excess_inventory_initial_guess = [2000, 350, 700, 150, 400]
ROP_initial_guess = [1000, 250, 200, 150, 200]
guess_vec = excess_inventory_initial_guess + ROP_initial_guess # concatenate lists
guess = []
for j in range(len(guess_vec)):
    g = (0, guess_vec[j])
    guess.append(g)

In [51]:
NUM_CYCLES = 5 #1000
TIME_LIMIT = 10 # 1440 minutes
start_time = time.time()
print("\nMax time limit: " + str(TIME_LIMIT) + " minutes")
print("Max algorithm cycles: " + str(NUM_CYCLES) + " (20 iterations per cycle)")
print("The algorithm will run either for " + str(TIME_LIMIT) + " minutes or " + str(NUM_CYCLES) + " cycles")


Max time limit: 10 minutes
Max algorithm cycles: 5 (20 iterations per cycle)
The algorithm will run either for 10 minutes or 5 cycles


### GP Minimize Lost Sales Optimization

In [52]:
ctr = 1
start_time=time.time()
elapsed_time = (time.time() - start_time)/60.0
bestObj = 1e7
bestSoln = []
bestCycle = 0
while ctr <= NUM_CYCLES and elapsed_time <= TIME_LIMIT:
    print('\nCycle: ' + str(ctr))
    print('{0:4s}    {1:9s}'.format('Iter', 'Obj'))
    """
    opt = forest_minimize(func=getObj
                        , dimensions=guess
                        , n_calls=20
                        , n_random_starts=10
                        , random_state=707
                        , verbose=False
                        , callback=callbackF
                        , kappa=50)
    """
    opt = gp_minimize(func=getObj_GP_minimize_lost_sales
                        , dimensions=guess
                        , n_calls=20
                        , n_random_starts=10
                        , random_state=ctr
                        , verbose=False
                        , callback=callbackF
                        , kappa=50)

    if opt.fun < bestObj:
        bestObj = opt.fun
        bestSoln = opt.x
        bestCycle = ctr
    ctr += 1
    elapsed_time = (time.time() - start_time)/60.0


Cycle: 1
Iter    Obj      
------------------------------Total Service Level------------------------------------------
[0.         0.93412558 0.92745261 0.         0.98635125 0.84701245]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 1008.6854764950906, 169.00172677316283, 44.83928286312074, 135.0165695262991, 94.65559172852026]
Total On hand: 1452.1986473861934
------------------------------Total Service Level------------------------------------------
[0.         1.87402054 1.78988568 0.         1.71092131 1.43185237]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 1095.0712371718153, 154.85089776595143, 91.04294517168933, 96.77766995507518, 60.430362576189836]
Total On hand: 2950.3717600269147
------------------------------Total Service Level------------------------------------------
[0.         2.84476417 2.66651488 0.         1.78743528 1.483

------------------------------Total Service Level------------------------------------------
[0.         0.97988037 0.90587771 0.         1.         0.91820529]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 902.8834650448918, 110.92525798751716, 137.46583538466703, 126.11117120294082, 143.04838740949882]
Total On hand: 1420.4341170295156
------------------------------Total Service Level------------------------------------------
[0.         1.97988037 1.72903286 0.         1.98617518 1.72394171]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 827.6607733637709, 87.73364269424482, 131.09122880461956, 121.80903031764659, 138.0615104119054]
Total On hand: 2726.7903026217027
------------------------------Total Service Level------------------------------------------
[0.         2.96683533 2.61700246 0.         2.9799354  2.57866478]
--------------------

------------------------------Total Service Level------------------------------------------
[0.         4.         3.96881772 0.         0.16002413 0.23267099]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 1193.8185479587771, 234.35778597565658, 90.96033964475788, 1.5887177016494578, 9.248863557031438]
Total On hand: 6219.816101596605
------------------------------Total Service Level------------------------------------------
[0.         5.         4.96410887 0.         0.20743248 0.29536451]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 1206.9216095146685, 233.969695835711, 115.55788499221764, 1.6770623372470912, 15.379663143171062]
Total On hand: 7793.32201741962
------------------------------Total Service Level------------------------------------------
[0.         6.         5.95880687 0.         0.27959241 0.35460247]
-----------------------

------------------------------Total Service Level------------------------------------------
[0.         6.80050369 8.47454639 0.         3.51350166 7.2963633 ]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 468.80046729404285, 164.90539866457289, 117.77280151484875, 6.43875668283721, 92.15682282569281]
Total On hand: 7586.707306796701
------------------------------Total Service Level------------------------------------------
[0.         7.57678058 9.44017368 0.         3.90968379 8.14969375]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 432.9596746716961, 168.28431202405363, 129.4238165148029, 6.816269786300196, 99.83235205066609]
Total On hand: 8424.02373184422
------------------------------Total Service Level------------------------------------------
[ 0.          8.32766492 10.39769558  0.          4.28930262  9.0061701 ]
--------------------

------------------------------Total Service Level------------------------------------------
[0.         8.53016539 4.56097362 0.         5.18573207 7.61519651]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 786.6536316139532, 32.34374567294228, 209.95417518712827, 12.498063942789445, 59.3405670074894]
Total On hand: 9791.176071557085
------------------------------Total Service Level------------------------------------------
[0.         9.46697772 5.05501654 0.         5.74272193 8.4571376 ]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 747.5882144119615, 30.988733177506838, 195.55895097196156, 11.60866358462367, 58.41638810081318]
Total On hand: 10835.337021803953
------------------------------Total Service Level------------------------------------------
[ 0.         10.44461008  5.55934926  0.          6.29657482  9.30228371]
------------------

...

Per Node On hand: [0.0, 198.7601466939222, 193.48389681054073, 175.0168889684128, 115.04637760794792, 179.13897721116234]
Total On hand: 17343.815382355904
Service level penalty: [0.         0.3655975  0.0312555  0.         0.         0.04788145]
Objective Function value: 445601.6325962878
  95    124355.811449
------------------------------Total Service Level------------------------------------------
[0.         0.79548835 0.74924077 0.         0.96891235 0.88172722]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 862.5335326071987, 115.52777270675045, 74.44539381286238, 74.673644769107, 136.95468981281957]
Total On hand: 1264.1350337087383
------------------------------Total Service Level------------------------------------------
[0.         1.61318253 1.44918697 0.         1.87773609 1.72963798]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 80

  96    124355.811449
------------------------------Total Service Level------------------------------------------
[0.         0.85452527 1.         0.         0.33606944 0.83572614]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 838.7023180112125, 271.29980033516955, 139.49207287674585, 4.272306783658534, 119.81551201626863]
Total On hand: 1373.582010023055
------------------------------Total Service Level------------------------------------------
[0.         1.66375511 1.99966129 0.         0.63934265 1.62411765]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 843.1193512028659, 269.38761572010975, 108.75445081926162, 3.6925953453736327, 117.46425127495915]
Total On hand: 2716.000274385625
------------------------------Total Service Level------------------------------------------
[0.         2.50599659 2.97054487 0.         0.94849307 2.4693106 ]

------------------------------Total Service Level------------------------------------------
[0.         2.23272885 3.88133726 0.         3.74491212 3.35940021]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 264.6069503805452, 255.0888770744314, 81.03826345985004, 109.00663555216084, 126.09531646373904]
Total On hand: 3245.3259577242875
------------------------------Total Service Level------------------------------------------
[0.         2.81557506 4.84399638 0.         4.70029912 4.20268605]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 256.50835808280283, 241.38649255910292, 93.8192893047081, 117.86244053889297, 112.17471324651652]
Total On hand: 4067.077251456311
------------------------------Total Service Level------------------------------------------
[0.         3.37510303 5.82969322 0.         5.65213545 5.07641845]
----------------------

------------------------------Total Service Level------------------------------------------
[0.         6.24866088 6.82533144 0.         6.94638726 5.79629162]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 795.7797739598661, 223.38735634646497, 165.0456002810097, 116.06107213985763, 93.24134863670606]
Total On hand: 9926.018867938144
------------------------------Total Service Level------------------------------------------
[0.         7.14485369 7.81989099 0.         7.93799399 6.70299824]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 828.0683256077981, 232.44328070832853, 174.221817559026, 122.04804460720224, 105.70431990967627]
Total On hand: 11388.504656330177
------------------------------Total Service Level------------------------------------------
[0.         8.0153535  8.81262201 0.         8.93467433 7.5575483 ]
-----------------------

------------------------------Total Service Level------------------------------------------
[0.         6.28931901 6.94467826 0.         6.96174069 1.80979496]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 963.2887835523262, 266.9926202677413, 273.539123654367, 134.74077765027815, 3.014106546883458]
Total On hand: 11444.910179972116
------------------------------Total Service Level------------------------------------------
[0.         7.23083155 7.94467826 0.         7.96174069 2.07258332]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 944.8021612371948, 278.8191304545933, 271.1017932726233, 137.81776810879015, 2.7090815755167754]
Total On hand: 13080.160114620834
------------------------------Total Service Level------------------------------------------
[0.         8.10963516 8.92520982 0.         8.95008831 2.33356474]
------------------------

In [53]:
print("\nFinal objective: " + "{0:10.3f}".format(bestObj))
print("\nFinal solution: " + str(bestSoln))
print("\nBest cycle: " + str(bestCycle))
print("\nTotal time: " + "{0:3.2f}".format(elapsed_time) + " minutes")


Final objective:   1432.182

Final solution: [315, 208, 463, 19, 293, 896, 183, 96, 145, 192]

Best cycle: 1

Total time: 3.41 minutes


In [54]:
final_solution=bestSoln
final_inventory_stock = final_solution[:(numNodes - 1)]
final_ROP = final_solution[(numNodes - 1):]
print('Optimized Inventory Position',np.round(final_inventory_stock)) ## [ plant_area WH1  WH2 Store1 Store2]
print('Optimized Reoorder point',np.round(final_ROP))                 ## [ plant_area WH1  WH2 Store1 Store2]

Optimized Inventory Position [315 208 463  19 293]
Optimized Reoorder point [896 183  96 145 192]


### Predict GP Minimize Lost Sales Using Inputs and optimized values

In [76]:
guess_vec=np.round(bestSoln)
guess=[]
for j in range(len(guess_vec)):
    g = (0, guess_vec[j])
    guess.append(g)

In [77]:
opt = gp_minimize(func=predict_GP_minimize_lost_sales
                        , dimensions=guess
                        , n_calls=10
                        , n_random_starts=10
                        , random_state=ctr
                        , verbose=False
                        , callback=callbackF
                        , kappa=50)

------------------------------Total Service Level------------------------------------------
[0.         0.27666978 0.2340748  0.15082571 0.01034004 0.02124637]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 35.349444444444444, 10.195833333333333, 4.752222222222222, 0.5352777777777777, 4.391944444444444]
Total On hand: 55.224722222222226
------------------------------Total Service Level------------------------------------------
[0.         0.54660606 0.4810522  0.28837822 0.02026056 0.04269208]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 37.51638888888889, 11.4, 3.8216666666666663, 0.31, 4.223333333333334]
Total On hand: 112.49611111111112
------------------------------Total Service Level------------------------------------------
[0.         0.80210503 0.71867915 0.43650999 0.0306362  0.06421811]
------------------------------Total Average on H

------------------------------Total Service Level------------------------------------------
[0.         0.99842887 0.28949454 0.26167988 0.02765688 0.02294816]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 483.99333333333334, 15.503888888888888, 15.738333333333333, 2.1616666666666666, 2.841666666666667]
Total On hand: 520.2388888888888
------------------------------Total Service Level------------------------------------------
[0.         1.98507769 0.57925161 0.51827783 0.05446804 0.0455888 ]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 492.24972222222226, 15.896666666666667, 13.252500000000001, 1.1916666666666667, 2.6944444444444446]
Total On hand: 1045.523888888889
------------------------------Total Service Level------------------------------------------
[0.         2.98175597 0.90334689 0.77447397 0.07110889 0.05816097]
-------------------

------------------------------Total Service Level------------------------------------------
[0.         1.8674479  0.20692331 0.56718854 0.00893769 0.03621268]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 272.6844444444444, 0.8702777777777778, 21.899444444444445, 0.11, 1.6619444444444447]
Total On hand: 597.9458333333333
------------------------------Total Service Level------------------------------------------
[0.         2.77250291 0.30456975 0.70677991 0.05655077 0.19586932]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 270.62444444444446, 1.4147222222222222, 9.004444444444443, 0.8377777777777778, 13.970277777777778]
Total On hand: 893.7975
------------------------------Total Service Level------------------------------------------
[0.         3.6729302  0.3978085  0.99840415 0.06063782 0.21332999]
------------------------------Total Average

------------------------------Total Service Level------------------------------------------
[0.         3.55111749 2.74863882 1.23160373 0.55187347 2.10694172]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 305.8927777777779, 63.94861111111111, 16.178888888888892, 0.9783333333333333, 42.86555555555556]
Total On hand: 2018.6180555555557
------------------------------Total Service Level------------------------------------------
[0.         4.20916149 3.29524304 1.47256442 0.66723661 2.53137673]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 293.7897222222222, 68.5513888888889, 19.382777777777783, 1.9816666666666667, 47.25222222222222]
Total On hand: 2449.5758333333333
------------------------------Total Service Level------------------------------------------
[0.         4.91599981 3.84431279 1.71494852 0.76567865 2.94524796]
-----------------------

------------------------------Total Service Level------------------------------------------
[0.         4.90260866 1.40744827 1.40028429 0.19506971 2.7546703 ]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 294.82944444444126, 9.845555555555556, 37.47944444444445, 0.06777777777777777, 69.76]
Total On hand: 2446.1302777777764
------------------------------Total Service Level------------------------------------------
[0.         5.73534159 1.64147897 1.61704844 0.22630391 3.26481462]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 282.23111111111103, 10.837222222222222, 27.209444444444447, 0.14555555555555555, 66.195]
Total On hand: 2832.7486111111098
------------------------------Total Service Level------------------------------------------
[0.         6.57995215 1.88731187 1.87880031 0.26101745 3.7032475 ]
------------------------------Total Avera

------------------------------Total Service Level------------------------------------------
[0.         3.0312898  1.53456064 1.21493318 0.0781046  0.0776593 ]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 67.61611111111112, 13.590277777777779, 8.032777777777778, 0.45333333333333337, 3.9227777777777786]
Total On hand: 599.635
------------------------------Total Service Level------------------------------------------
[0.         3.53500265 1.77905892 1.41068764 0.09318314 0.09034786]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 77.83583333333334, 14.099722222222221, 8.556111111111111, 0.31333333333333335, 1.7222222222222228]
Total On hand: 702.1622222222222
------------------------------Total Service Level------------------------------------------
[0.         4.0354768  2.03562526 1.63766254 0.10482968 0.10328253]
------------------------------

------------------------------Total Service Level------------------------------------------
[0.         2.71850845 1.1880029  0.65350378 0.53104095 0.64680405]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 45.00777777777779, 21.432222222222222, 8.432777777777776, 3.245, 7.411666666666667]
Total On hand: 610.9205555555556
------------------------------Total Service Level------------------------------------------
[0.         3.04631151 1.4012305  0.76140101 0.61466677 0.73984689]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 45.23527777777777, 21.423333333333332, 16.08416666666667, 3.798333333333334, 8.097222222222221]
Total On hand: 705.5588888888889
------------------------------Total Service Level------------------------------------------
[0.         3.34434748 1.59686474 0.87426594 0.72887379 0.87255423]
------------------------------Total Av

------------------------------Total Service Level------------------------------------------
[0.         3.56421855 2.21085471 0.80618307 1.65932505 0.34526222]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 100.75999999999999, 25.114444444444448, 5.913333333333334, 9.932222222222222, 0.15166666666666667]
Total On hand: 923.0027777777777
------------------------------Total Service Level------------------------------------------
[0.         4.03211706 2.50575686 0.93039493 1.87866999 0.39317638]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 84.90861111111111, 23.003333333333334, 6.602222222222223, 8.29888888888889, 0.2897222222222222]
Total On hand: 1046.1055555555556
------------------------------Total Service Level------------------------------------------
[0.         4.53311478 2.78853394 1.05109506 2.10863596 0.44323045]
----------------------

------------------------------Total Service Level------------------------------------------
[0.         1.71629011 2.03001174 0.93240529 0.26445839 0.53932732]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 16.18888888888889, 15.411111111111111, 4.670555555555556, 0.6122222222222221, 2.787777777777778]
Total On hand: 395.12361111111113
------------------------------Total Service Level------------------------------------------
[0.         1.87802022 2.23896849 0.99471771 0.31434294 0.62385037]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 11.2325, 21.019444444444446, 2.8130555555555556, 0.7733333333333333, 6.405555555555556]
Total On hand: 437.3675
------------------------------Total Service Level------------------------------------------
[0.         2.10005243 2.43596801 1.12070431 0.32913617 0.6486366 ]
------------------------------Total Avera

------------------------------Total Service Level------------------------------------------
[0.         9.39959832 0.56119854 0.40357918 0.16800066 0.45815455]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 107.60944444444445, 3.3691666666666675, 6.369722222222223, 0.17555555555555558, 3.115]
Total On hand: 1525.3316666666697
------------------------------Total Service Level------------------------------------------
[ 0.         10.12185768  0.66047369  0.45946424  0.19742737  0.56739079]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 90.76972222222224, 10.619444444444444, 9.082777777777778, 0.4975, 12.303333333333333]
Total On hand: 1648.6044444444474
------------------------------Total Service Level------------------------------------------
[ 0.         10.71977484  0.79072656  0.54440255  0.23814718  0.7005749 ]
------------------------------T

In [78]:
bestObj = opt.fun
bestSoln = opt.x
bestCycle = ctr
print("\nFinal objective: " + "{0:10.3f}".format(bestObj))
print("\nFinal solution: " + str(bestSoln))
print("\nBest cycle: " + str(bestCycle))
print("\nTotal time: " + "{0:3.2f}".format(elapsed_time) + " minutes")


Final objective: 2014373.425

Final solution: [145, 114, 365, 14, 211, 715, 161, 79, 44, 143]

Best cycle: 6

Total time: 3.41 minutes


In [79]:
final_solution=bestSoln
final_inventory_stock = final_solution[:(numNodes - 1)]
final_ROP = final_solution[(numNodes - 1):]
print('Optimized Inventory Position',np.round(final_inventory_stock)) ## [ plant_area WH1  WH2 Store1 Store2]
print('Optimized Reoorder point',np.round(final_ROP))                 ## [ plant_area WH1  WH2 Store1 Store2]

Optimized Inventory Position [145 114 365  14 211]
Optimized Reoorder point [715 161  79  44 143]


### GP Minimize Back Order Optimization

In [83]:
ctr = 1
start_time=time.time()
elapsed_time = (time.time() - start_time)/60.0
bestObj = 1e7
bestSoln = []
bestCycle = 0
while ctr <= NUM_CYCLES and elapsed_time <= TIME_LIMIT:
    print('\nCycle: ' + str(ctr))
    print('{0:4s}    {1:9s}'.format('Iter', 'Obj'))
    """
    opt = forest_minimize(func=getObj
                        , dimensions=guess
                        , n_calls=20
                        , n_random_starts=10
                        , random_state=707
                        , verbose=False
                        , callback=callbackF
                        , kappa=50)
    """
    opt = gp_minimize(func=getObj_GP_minimize_back_order
                        , dimensions=guess
                        , n_calls=20
                        , n_random_starts=10
                        , random_state=ctr
                        , verbose=False
                        , callback=callbackF
                        , kappa=50)

    if opt.fun < bestObj:
        bestObj = opt.fun
        bestSoln = opt.x
        bestCycle = ctr
    ctr += 1
    elapsed_time = (time.time() - start_time)/60.0


Cycle: 1
Iter    Obj      
------------------------------Total Service Level------------------------------------------
[1.         0.83414251 0.65760431 1.         0.13404626 0.03625542]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 196.65125566939608, 53.24530980910602, 109.09786296132944, 9.823863430018323, 4.555586230341226]
Total On hand: 373.3738781001911
------------------------------Total Service Level------------------------------------------
[2.         1.56058689 1.18964439 2.         0.20936838 0.07408902]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 200.37824631506194, 40.47906606140674, 115.77223120592882, 6.852282349541129, 3.8306041464956193]
Total On hand: 740.6863081786254
------------------------------Total Service Level------------------------------------------
[3.         2.24243095 1.80656976 3.         0.269832   0.12629

------------------------------Total Service Level------------------------------------------
[3.         2.9362855  1.5116752  3.         1.32330147 0.85490361]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 526.1634412180169, 25.870204991469603, 87.10650576412127, 61.314939805202116, 49.625780863293016]
Total On hand: 2377.222457995156
------------------------------Total Service Level------------------------------------------
[4.         3.92117314 1.9641931  4.         1.57302886 0.98995644]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 581.7811787075741, 20.73685563557579, 169.21373694866654, 24.090092751232618, 10.456032700824986]
Total On hand: 3183.50035473903
------------------------------Total Service Level------------------------------------------
[5.         4.92098431 2.52322382 5.         1.68272217 1.0392299 ]
-----------------------

------------------------------Total Service Level------------------------------------------
[3.         2.96742529 2.73476956 3.         0.03299062 0.13736025]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 622.2518988220542, 119.73289531290624, 67.36625155175606, 0.11986519423541177, 5.9611047967681445]
Total On hand: 2383.007143030896
------------------------------Total Service Level------------------------------------------
[4.         3.95345481 3.66725282 4.         0.04322136 0.17953183]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 571.3187018939394, 120.06037189244813, 44.43249999999999, 0.1067428931664637, 7.685325698994469]
Total On hand: 3126.6107854094444
------------------------------Total Service Level------------------------------------------
[5.         4.94355375 4.56512335 5.         0.05298867 0.22781379]
---------------------

------------------------------Total Service Level------------------------------------------
[4.         0.4636972  1.32709644 4.         0.29269529 0.47391709]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 2.101717872136588, 36.374034005952886, 15.263878675836988, 0.03174289316646369, 5.4205264032244145]
Total On hand: 227.0324663870079
------------------------------Total Service Level------------------------------------------
[5.         0.56590576 1.57350933 5.         0.36678173 0.66089352]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 3.3286996819061465, 12.693244058884915, 23.890126962839624, 0.0225, 9.551482832540271]
Total On hand: 276.51851992317887
------------------------------Total Service Level------------------------------------------
[6.         0.67867684 2.09035372 6.         0.4239816  0.77639111]
------------------------------

------------------------------Total Service Level------------------------------------------
[5.         3.55594567 0.75363504 5.         0.71179182 1.02307793]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 208.09045853018762, 0.7499860220777445, 90.90815768532856, 0.05440299240007303, 4.169300288105843]
Total On hand: 1354.3923425304356
------------------------------Total Service Level------------------------------------------
[6.         4.15084769 0.87464189 6.         0.84831483 1.19077748]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 165.2911409565545, 0.5157286262841178, 80.02409706926676, 0.3391057515613645, 2.5641313047517573]
Total On hand: 1603.1265462388542
------------------------------Total Service Level------------------------------------------
[7.         4.81488527 1.01197658 7.         0.97408989 1.4012875 ]
-------------------

...

C:\Users\kishore.kukreja\AppData\Roaming\Python\Python38\site-packages\skopt\optimizer\optimizer.py:449: UserWarning: The objective has been evaluated at this point before.
  warnings.warn("The objective has been evaluated "


------------------------------Total Service Level------------------------------------------
[2.         1.81509995 1.91982711 2.         2.         1.88869286]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 576.4642552498925, 155.15442482388735, 165.31663289769685, 111.06680020801376, 120.33454322755004]
Total On hand: 2261.264220153549
------------------------------Total Service Level------------------------------------------
[3.         2.71862608 2.85798315 3.         3.         2.80469078]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 570.2898978794385, 162.450774578456, 145.34349904665007, 113.07183412935521, 104.03680112512181]
Total On hand: 3356.4570269125707
------------------------------Total Service Level------------------------------------------
[4.         3.64976508 3.85550801 4.         3.99086097 3.67746863]
---------------------

------------------------------Total Service Level------------------------------------------
[3.         2.99269201 2.94166997 3.         0.34106565 0.16205688]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 776.6794645073575, 170.36021860271407, 88.89361111111111, 5.8232625326267025, 1.7982414976783139]
Total On hand: 3096.7476557477094
------------------------------Total Service Level------------------------------------------
[4.         3.99269201 3.9055767  4.         0.50887592 0.21768922]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 760.4058035701206, 159.9505662432875, 71.87972222222223, 9.209997848450913, 2.7472645968851346]
Total On hand: 4100.941010228676
------------------------------Total Service Level------------------------------------------
[5.         4.9922861  4.87589334 5.         0.67656815 0.3021644 ]
-----------------------

------------------------------Total Service Level------------------------------------------
[3.         2.86087384 1.12509904 3.         0.44373008 2.78542106]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 589.1355245157704, 21.503569316974527, 187.97209021795555, 0.09377828360311408, 114.30176262181226]
Total On hand: 2749.8510286736246
------------------------------Total Service Level------------------------------------------
[4.         3.78343502 1.50197843 4.         0.59441514 3.69739909]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 560.0821724871353, 19.215343474238527, 200.0004370193057, 0.0781162753220413, 114.152859605891]
Total On hand: 3643.379957535517
------------------------------Total Service Level------------------------------------------
[5.         4.72958364 1.89013188 5.         0.73220486 4.65598123]
---------------------

------------------------------Total Service Level------------------------------------------
[3.         2.81565714 2.92676032 3.         2.99678551 2.73286618]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 562.792519221128, 155.64580006887542, 163.99200007779183, 120.62558357238973, 110.52838730012681]
Total On hand: 3335.4006419715934
------------------------------Total Service Level------------------------------------------
[4.         3.76231916 3.88648345 4.         3.99678551 3.645415  ]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 555.3634365719083, 131.64392426184463, 158.8326353336004, 121.29209619932318, 110.14825621813041]
Total On hand: 4412.6809905564005
------------------------------Total Service Level------------------------------------------
[5.         4.68583917 4.84758507 5.         4.99678551 4.57878529]
--------------------

In [85]:
print("\nFinal objective: " + "{0:10.3f}".format(bestObj))
print("\nFinal solution: " + str(bestSoln))
print("\nBest cycle: " + str(bestCycle))
print("\nTotal time: " + "{0:3.2f}".format(elapsed_time) + " minutes")


Final objective:   9610.170

Final solution: [315, 174, 463, 19, 0, 896, 183, 96, 145, 192]

Best cycle: 2

Total time: 3.47 minutes


In [86]:
final_solution=bestSoln
final_inventory_stock = final_solution[:(numNodes - 1)]
final_ROP = final_solution[(numNodes - 1):]
print('Optimized Inventory Position',np.round(final_inventory_stock)) ## [ plant_area WH1  WH2 Store1 Store2]
print('Optimized Reoorder point',np.round(final_ROP))                 ## [ plant_area WH1  WH2 Store1 Store2]

Optimized Inventory Position [315 174 463  19   0]
Optimized Reoorder point [896 183  96 145 192]


### Predict GP Minimize Back Order Using Inputs and optimized values

In [93]:
guess_vec=np.round(bestSoln)
guess=[]
for j in range(len(guess_vec)):
    if guess_vec[j]==0:
        guess_vec[j]=1
    
    g = (0, guess_vec[j])
    guess.append(g)

In [94]:
guess

[(0, 315),
 (0, 174),
 (0, 463),
 (0, 19),
 (0, 1),
 (0, 896),
 (0, 183),
 (0, 96),
 (0, 145),
 (0, 192)]

In [95]:
opt = gp_minimize(func=predict_GP_minimize_back_order
                        , dimensions=guess
                        , n_calls=10
                        , n_random_starts=10
                        , random_state=ctr
                        , verbose=False
                        , callback=callbackF
                        , kappa=50)

------------------------------Total Service Level------------------------------------------
[1.         0.15725915 0.08858706 0.07224746 0.01065973 0.01684646]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 2.5236111111111112, 0.5572222222222223, 0.2025, 0.235, 0.8708333333333333]
Total On hand: 4.389166666666667
------------------------------Total Service Level------------------------------------------
[2.         0.31398773 0.17409808 0.14645587 0.02096836 0.03601768]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 2.728888888888889, 0.7525000000000001, 0.23555555555555557, 0.1925, 0.6869444444444444]
Total On hand: 8.985555555555557
------------------------------Total Service Level------------------------------------------
[3.         0.47461979 0.27021551 0.2119425  0.02912378 0.04887548]
------------------------------Total Average on Hand----

------------------------------Total Service Level------------------------------------------
[1.         0.98101638 0.11866291 0.00855009 0.13430259 0.09386748]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 422.8861111111111, 0.7541666666666667, 0.6983333333333335, 0.34500000000000003, 0.5427777777777779]
Total On hand: 425.2263888888889
------------------------------Total Service Level------------------------------------------
[2.         1.93643096 0.23022192 0.01525836 0.25673568 0.2029701 ]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 437.3413888888889, 0.9708333333333333, 0.6188888888888889, 0.5061111111111112, 0.3616666666666667]
Total On hand: 865.0252777777778
------------------------------Total Service Level------------------------------------------
[3.         2.91571057 0.35458617 0.02124315 0.37206293 0.28944897]
-------------------

------------------------------Total Service Level------------------------------------------
[1.         0.84813556 0.07942651 0.00981994 0.06254276 0.10927211]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 238.78833333333336, 0.10500000000000001, 0.8119444444444445, 0.21444444444444447, 0.7119444444444443]
Total On hand: 240.63166666666666
------------------------------Total Service Level------------------------------------------
[2.         1.68090223 0.16410258 0.01919354 0.11762706 0.2343382 ]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 214.5613888888889, 0.10500000000000001, 0.7925, 0.14500000000000002, 0.903611111111111]
Total On hand: 457.13916666666665
------------------------------Total Service Level------------------------------------------
[3.         2.51710671 0.24176987 0.0258064  0.17154863 0.36032231]
--------------------------

------------------------------Total Service Level------------------------------------------
[5.         2.87404858 0.57133424 0.51871195 0.41673984 0.86280766]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 192.98055555555555, 1.3794444444444445, 2.6900000000000004, 0.23222222222222225, 0.5494444444444444]
Total On hand: 919.5638888888889
------------------------------Total Service Level------------------------------------------
[6.         3.48574602 0.69441265 0.61064893 0.5188993  1.04897111]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 188.9438888888889, 1.7138888888888888, 3.755555555555556, 0.14500000000000002, 0.716111111111111]
Total On hand: 1114.8383333333334
------------------------------Total Service Level------------------------------------------
[7.         4.03727243 0.81990497 0.71838543 0.602897   1.2612248 ]
------------------

------------------------------Total Service Level------------------------------------------
[5.         2.98780498 0.55964694 0.45014489 0.14361279 0.82996769]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 158.89833333333334, 0.5108333333333333, 4.291944444444445, 0.04, 1.55]
Total On hand: 862.4877777777779
------------------------------Total Service Level------------------------------------------
[6.         3.61150958 0.68068571 0.54085438 0.17381072 0.97820436]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 177.99888888888887, 0.4905555555555555, 2.955277777777778, 0.04, 1.0916666666666666]
Total On hand: 1045.0641666666668
------------------------------Total Service Level------------------------------------------
[7.         4.24358034 0.78373172 0.62137644 0.20183891 1.1248948 ]
------------------------------Total Average on Hand----------

------------------------------Total Service Level------------------------------------------
[7.         1.02346566 0.60708904 0.03466271 0.26817082 0.50948496]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 3.029444444444444, 0.6819444444444445, 0.5391666666666667, 0.3672222222222223, 0.29888888888888887]
Total On hand: 35.5375
------------------------------Total Service Level------------------------------------------
[8.         1.14353677 0.69014817 0.04077787 0.30527333 0.58303873]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 3.067777777777778, 0.7097222222222223, 0.3672222222222223, 0.2688888888888889, 0.3738888888888889]
Total On hand: 40.325
------------------------------Total Service Level------------------------------------------
[9.         1.29721707 0.78260916 0.047396   0.33458368 0.64880304]
------------------------------Total Aver

------------------------------Total Service Level------------------------------------------
[7.         1.12625747 0.14132382 0.08284588 0.06524087 0.07462361]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 9.090277777777779, 2.6694444444444443, 3.6283333333333334, 0.22250000000000003, 0.36888888888888893]
Total On hand: 79.81277777777778
------------------------------Total Service Level------------------------------------------
[8.         1.46697997 0.16130298 0.09432475 0.07336749 0.08388709]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 28.24888888888889, 2.7944444444444443, 3.1747222222222224, 0.2255555555555556, 0.265]
Total On hand: 114.52138888888891
------------------------------Total Service Level------------------------------------------
[9.         1.61853563 0.1844051  0.10674625 0.0800625  0.09078953]
------------------------------

------------------------------Total Service Level------------------------------------------
[8.         1.33957829 0.75828749 0.69036292 0.69977655 0.37536544]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 7.424166666666666, 1.238888888888889, 1.1477777777777778, 0.3966666666666667, 0.0425]
Total On hand: 90.23666666666668
------------------------------Total Service Level------------------------------------------
[9.         1.48826891 0.84145125 0.7685444  0.79234786 0.42382789]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 4.864166666666667, 0.6172222222222222, 1.6005555555555557, 0.30888888888888894, 0.0425]
Total On hand: 97.67000000000002
------------------------------Total Service Level------------------------------------------
[10.          1.63377165  0.92228139  0.86011737  0.87444567  0.4654795 ]
------------------------------Total Av

------------------------------Total Service Level------------------------------------------
[9.         0.74625469 0.67613215 0.06700644 0.41643293 0.75283691]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 2.279166666666667, 1.4527777777777777, 1.0566666666666669, 0.11499999999999999, 0.33499999999999996]
Total On hand: 39.61472222222223
------------------------------Total Service Level------------------------------------------
[10.          0.84788021  0.755819    0.07644673  0.45752207  0.82573925]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 1.335, 1.1122222222222222, 0.6066666666666668, 0.18, 0.43305555555555547]
Total On hand: 43.28166666666667
------------------------------Total Service Level------------------------------------------
[11.          0.90870203  0.8392124   0.08687533  0.49600552  0.92056152]
------------------------------T

------------------------------Total Service Level------------------------------------------
[1.00000000e+01 1.96332041e+00 1.37936276e-01 2.21995478e-01
 7.45758714e-02 7.37075047e-03]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 15.358055555555557, 1.0225, 5.183055555555556, 0.35944444444444446, 0.015000000000000001]
Total On hand: 143.96
------------------------------Total Service Level------------------------------------------
[1.10000000e+01 2.13652928e+00 1.55134358e-01 2.47276049e-01
 8.50465073e-02 8.32394892e-03]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 5.841388888888891, 1.061388888888889, 5.193611111111111, 0.22555555555555556, 0.018888888888888893]
Total On hand: 156.30083333333334
------------------------------Total Service Level------------------------------------------
[1.20000000e+01 2.28285645e+00 1.67370606e-01 2.71169043

In [96]:
bestObj = opt.fun
bestSoln = opt.x
bestCycle = ctr
print("\nFinal objective: " + "{0:10.3f}".format(bestObj))
print("\nFinal solution: " + str(bestSoln))
print("\nBest cycle: " + str(bestCycle))
print("\nTotal time: " + "{0:3.2f}".format(elapsed_time) + " minutes")


Final objective: 2515248.220

Final solution: [238, 68, 111, 3, 1, 819, 87, 65, 116, 88]

Best cycle: 6

Total time: 3.47 minutes


In [97]:
final_solution=bestSoln
final_inventory_stock = final_solution[:(numNodes - 1)]
final_ROP = final_solution[(numNodes - 1):]
print('Optimized Inventory Position',np.round(final_inventory_stock)) ## [ plant_area WH1  WH2 Store1 Store2]
print('Optimized Reoorder point',np.round(final_ROP))                 ## [ plant_area WH1  WH2 Store1 Store2]

Optimized Inventory Position [238  68 111   3   1]
Optimized Reoorder point [819  87  65 116  88]


### Insights

In [ ]:
Lost Sales
Optimized Inventory Position [315 208 463  19 293]
Optimized Reoorder point [896 183  96 145 192]

Back Order
Optimized Inventory Position [1067  108  608  132   50]
Optimized Reoorder point [839 201 144 100 189]

## rbfOpt Black-Box Derivative Free

### rbfOpt Black-Box Define Function

In [99]:
def getObj_rbfOpt_lost_sales(initial_guess):

    # Split the initial guess to get base stock and ROP
    excess_inventory_guess = initial_guess[:(numNodes - 1)]
    ROP_guess = initial_guess[(numNodes - 1):]
    base_stock_guess = np.add(excess_inventory_guess, ROP_guess)
    
    # Insert the supply node's base stock
    baseStock = np.insert(base_stock_guess, 0, 10000)
    
    # Insert a zero ROP for the first source node
    ROP = np.insert(ROP_guess, 0, 0)
    
    # Initialize inventory level
    initialInv = 0.9*baseStock
    
    replications = 20
    totServiceLevel = np.zeros(numNodes)
    totAvgOnHand = 0.0
    for i in range(replications):
        nodes = lost_sales_simulate(i,numNodes,nodeNetwork,initialInv,ROP,baseStock,\
                                 demandAllNodes,defaultLeadTime,leadTimeDelay)
        print('------------------------------Total Service Level------------------------------------------')
        totServiceLevel = np.array([totServiceLevel[j] + \
                                    nodes[j].serviceLevel for j in range(len(nodes))]) #convert list to array
        print(totServiceLevel)
        totAvgOnHand += np.sum([nodes[j].avgOnHand for j in range(len(nodes))])
        print('------------------------------Total Average on Hand------------------------------------------')
        print('Per Node On hand:',[nodes[j].avgOnHand for j in range(len(nodes))])
        print('Total On hand:',totAvgOnHand)
    servLevelPenalty = np.maximum(0, serviceTarget - totServiceLevel/replications) # element-wise max
    print('Service level penalty:',servLevelPenalty)
    objFunValue = totAvgOnHand/replications + 1.0e6*np.sum(servLevelPenalty)
    print('Objective Function value:',objFunValue)
    return objFunValue

In [100]:
def getObj_rbfOpt_back_order(initial_guess):

    # Split the initial guess to get base stock and ROP
    excess_inventory_guess = initial_guess[:(numNodes - 1)]
    ROP_guess = initial_guess[(numNodes - 1):]
    base_stock_guess = np.add(excess_inventory_guess, ROP_guess)
    
    # Insert the supply node's base stock
    baseStock = np.insert(base_stock_guess, 0, 10000)
    
    # Insert a zero ROP for the first source node
    ROP = np.insert(ROP_guess, 0, 0)
    
    # Initialize inventory level
    initialInv = 0.9*baseStock
    
    replications = 20
    totServiceLevel = np.zeros(numNodes)
    totAvgOnHand = 0.0
    for i in range(replications):
        nodes = back_order_simulate(i,numNodes,nodeNetwork,initialInv,ROP,baseStock,\
                                 demandAllNodes,defaultLeadTime,leadTimeDelay)
        print('------------------------------Total Service Level------------------------------------------')
        totServiceLevel = np.array([totServiceLevel[j] + \
                                    nodes[j].serviceLevel for j in range(len(nodes))]) #convert list to array
        print(totServiceLevel)
        totAvgOnHand += np.sum([nodes[j].avgOnHand for j in range(len(nodes))])
        print('------------------------------Total Average on Hand------------------------------------------')
        print('Per Node On hand:',[nodes[j].avgOnHand for j in range(len(nodes))])
        print('Total On hand:',totAvgOnHand)
    servLevelPenalty = np.maximum(0, serviceTarget - totServiceLevel/replications) # element-wise max
    print('Service level penalty:',servLevelPenalty)
    objFunValue = totAvgOnHand/replications + 1.0e6*np.sum(servLevelPenalty)
    print('Objective Function value:',objFunValue)
    return objFunValue

In [101]:
def predict_rbfOpt_lost_sales(initial_guess):

    # Split the initial guess to get base stock and ROP
    excess_inventory_guess = initial_guess[:(numNodes - 1)]
    ROP_guess = initial_guess[(numNodes - 1):]
    base_stock_guess = np.add(excess_inventory_guess, ROP_guess)
    
    # Insert the supply node's base stock
    baseStock = np.insert(base_stock_guess, 0, 10000)
    
    # Insert a zero ROP for the first source node
    ROP = np.insert(ROP_guess, 0, 0)
    
    # Initialize inventory level
    initialInv = 0.9*baseStock
    
    replications = 20
    demand_input=np.random.randint(1,100,(replications,numNodes-1))
    leadtime_input=np.random.randint(1,5,replications)
    totServiceLevel = np.zeros(numNodes)
    totAvgOnHand = 0.0
    for i in range(replications):
        nodes = lost_sales_simulate(i,numNodes,nodeNetwork,initialInv,ROP,baseStock,\
                                 demand_input,defaultLeadTime,leadtime_input)
        print('------------------------------Total Service Level------------------------------------------')
        totServiceLevel = np.array([totServiceLevel[j] + \
                                    nodes[j].serviceLevel for j in range(len(nodes))]) #convert list to array
        print(totServiceLevel)
        totAvgOnHand += np.sum([nodes[j].avgOnHand for j in range(len(nodes))])
        print('------------------------------Total Average on Hand------------------------------------------')
        print('Per Node On hand:',[nodes[j].avgOnHand for j in range(len(nodes))])
        print('Total On hand:',totAvgOnHand)
    servLevelPenalty = np.maximum(0, serviceTarget - totServiceLevel/replications) # element-wise max
    print('Service level penalty:',servLevelPenalty)
    objFunValue = totAvgOnHand/replications + 1.0e6*np.sum(servLevelPenalty)
    print('Objective Function value:',objFunValue)
    return objFunValue

In [102]:
def predict_rbfOpt_back_order(initial_guess):

    # Split the initial guess to get base stock and ROP
    excess_inventory_guess = initial_guess[:(numNodes - 1)]
    ROP_guess = initial_guess[(numNodes - 1):]
    base_stock_guess = np.add(excess_inventory_guess, ROP_guess)
    
    # Insert the supply node's base stock
    baseStock = np.insert(base_stock_guess, 0, 10000)
    
    # Insert a zero ROP for the first source node
    ROP = np.insert(ROP_guess, 0, 0)
    
    # Initialize inventory level
    initialInv = 0.9*baseStock
    
    replications = 20
    demand_input=np.random.randint(1,100,(replications,numNodes-1))
    leadtime_input=np.random.randint(1,5,replications)
    totServiceLevel = np.zeros(numNodes)
    totAvgOnHand = 0.0
    for i in range(replications):
        nodes = back_order_simulate(i,numNodes,nodeNetwork,initialInv,ROP,baseStock,\
                                 demand_input,defaultLeadTime,leadtime_input)
        print('------------------------------Total Service Level------------------------------------------')
        totServiceLevel = np.array([totServiceLevel[j] + \
                                    nodes[j].serviceLevel for j in range(len(nodes))]) #convert list to array
        print(totServiceLevel)
        totAvgOnHand += np.sum([nodes[j].avgOnHand for j in range(len(nodes))])
        print('------------------------------Total Average on Hand------------------------------------------')
        print('Per Node On hand:',[nodes[j].avgOnHand for j in range(len(nodes))])
        print('Total On hand:',totAvgOnHand)
    servLevelPenalty = np.maximum(0, serviceTarget - totServiceLevel/replications) # element-wise max
    print('Service level penalty:',servLevelPenalty)
    objFunValue = totAvgOnHand/replications + 1.0e6*np.sum(servLevelPenalty)
    print('Objective Function value:',objFunValue)
    return objFunValue

### rbfOpt Black-Box Control Parameters

In [103]:
######## Main statements to call optimization ########
excess_inventory_initial_guess = [2000, 350, 700, 150, 400]
ROP_initial_guess = [1000, 250, 200, 150, 200]
guess = excess_inventory_initial_guess + ROP_initial_guess # concatenate lists
numVars = len(guess)
guess,numVars

([2000, 350, 700, 150, 400, 1000, 250, 200, 150, 200], 10)

In [104]:
settings = rbfopt.RbfoptSettings(max_evaluations=50,#5000
                                global_search_method='solver',
                                rand_seed=707,
                                minlp_solver_path=r"C:\Users\kishore.kukreja\Desktop\Inventory Policy Two Echelon\multi-echelon-inventory-optimization\bonmin-win64\bonmin.exe",
                                nlp_solver_path=r"C:\Users\kishore.kukreja\Desktop\Inventory Policy Two Echelon\multi-echelon-inventory-optimization\ipopt-win64\ipopt.exe")

### rbfOpt Black-Box Lost Sales Optimization

In [105]:
start_time = time.time()
bb = rbfopt.RbfoptUserBlackBox(numVars, np.array([0] * numVars), np.array(guess),
                               np.array(['R'] * numVars), getObj_rbfOpt_lost_sales)
alg = rbfopt.RbfoptAlgorithm(settings, bb)
val, x, itercount, evalcount, fast_evalcount = alg.optimize()
elapsed_time = (time.time() - start_time)/60.0

  Iter  Cycle  Action             Objective value      Time      Gap
  ----  -----  ------             ---------------      ----      ---
------------------------------Total Service Level------------------------------------------
[0.         0.8132005  0.61040585 0.         0.71460429 0.48011209]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 472.8987786419928, 39.20427776530132, 160.42050012041594, 46.75983982209889, 33.169611527241074]
Total On hand: 752.45300787705
------------------------------Total Service Level------------------------------------------
[0.         1.65826699 1.14143318 0.         1.3630451  0.99121404]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 476.56491983916106, 37.837664459433164, 156.7977195620269, 42.22650479897966, 39.852775451363726]
Total On hand: 1505.7325919880145
------------------------------Total Service Le

------------------------------Total Service Level------------------------------------------
[0.         2.77129522 2.90397896 0.         1.9086495  2.64805868]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 664.4217157205034, 147.3349838897486, 314.6533682253407, 18.052251748392944, 127.38621692626532]
Total On hand: 3888.7942837973756
------------------------------Total Service Level------------------------------------------
[0.         3.71367979 3.88227152 0.         2.59337446 3.55485663]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 664.6305680628129, 160.8713701319804, 314.23750015173096, 20.029441362830973, 124.5734253157426]
Total On hand: 5173.136588822474
------------------------------Total Service Level------------------------------------------
[0.         4.65488373 4.85855208 0.         3.25879206 4.44491806]
-----------------------

------------------------------Total Service Level------------------------------------------
[0.         3.97442333 3.62083263 0.         0.21235708 0.12913173]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 629.6801377926374, 134.13877459382957, 30.250659109455825, 4.915012964535517, 3.1528288559770243]
Total On hand: 3301.0220133654343
------------------------------Total Service Level------------------------------------------
[0.         4.93908918 4.55772179 0.         0.26113715 0.15990093]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 673.783914604143, 135.30956619727795, 30.328114566635087, 5.580562546325091, 5.493119543813795]
Total On hand: 4151.517290823629
------------------------------Total Service Level------------------------------------------
[0.         5.92827215 5.45989412 0.         0.31370064 0.19401935]
-----------------------

------------------------------Total Service Level------------------------------------------
[0.         3.03753321 3.58098627 0.         3.94745771 2.26086906]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 668.8361267576138, 123.2414614874239, 176.97290881400048, 81.38334571232011, 23.35095368110349]
Total On hand: 4009.7180882146713
------------------------------Total Service Level------------------------------------------
[0.         3.82962447 4.43535938 0.         4.94666454 2.81269278]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 644.7036706250586, 117.2357826785271, 159.78098638367027, 79.26878919423363, 26.71830131436381]
Total On hand: 5037.425618410525
------------------------------Total Service Level------------------------------------------
[0.         4.57038227 5.27803127 0.         5.9027295  3.40487874]
-------------------------

------------------------------Total Service Level------------------------------------------
[0.         5.41266247 4.58939511 0.         5.51195142 5.41035126]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 888.829809081075, 113.89534296814283, 285.74795866062647, 64.12263442189871, 183.36524253398753]
Total On hand: 9010.142969601799
------------------------------Total Service Level------------------------------------------
[0.         6.27939579 5.3032886  0.         6.46056085 6.31603688]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 852.0249490240197, 114.07183871697681, 266.6460349952381, 61.967908960518514, 189.4816118883148]
Total On hand: 10494.335313186866
------------------------------Total Service Level------------------------------------------
[0.         7.16132416 6.11163977 0.         7.3753363  7.20244116]
-----------------------

...

------------------------------Total Service Level------------------------------------------
[0.         0.99883953 0.99233144 0.         1.         0.97092523]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 1579.958986671743, 272.999625680587, 270.139510591447, 161.22853079313458, 149.85695904738216]
Total On hand: 2434.183612784294
------------------------------Total Service Level------------------------------------------
[0.         1.99500573 1.99078954 0.         1.99999999 1.92655963]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 1612.8832893369056, 257.458499609706, 264.2208223764871, 162.18430011247742, 182.14888412055035]
Total On hand: 4913.079408340421
------------------------------Total Service Level------------------------------------------
[0.         2.98109141 2.99023063 0.         2.99619507 2.84418703]
--------------------------

------------------------------Total Service Level------------------------------------------
[0.         0.99032378 1.         0.         0.99933276 0.92474413]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 1463.1145158088268, 247.84451044755644, 286.495834721133, 163.02839725795602, 168.80287775497328]
Total On hand: 2329.286135990446
------------------------------Total Service Level------------------------------------------
[0.         1.95990241 1.98908353 0.         1.96815319 1.90332701]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 1453.3272260795047, 241.67068891523078, 261.7406286194254, 141.5220952729581, 191.34029894365668]
Total On hand: 4618.887073821222
------------------------------Total Service Level------------------------------------------
[0.         2.89796107 2.98908353 0.         2.96160261 2.78644513]
----------------------

------------------------------Total Service Level------------------------------------------
[0.         0.99281676 0.99304528 0.         1.         0.95041501]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 1071.0024152810279, 274.7785676390072, 254.28592972100304, 161.33884504478584, 177.0886996107523]
Total On hand: 1938.494457296576
------------------------------Total Service Level------------------------------------------
[0.         1.94668384 1.98726995 0.         1.99999999 1.89363021]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 973.7874075190962, 256.63143307071954, 255.87828304006968, 163.70077968691572, 180.09134270307766]
Total On hand: 3768.583703316455
------------------------------Total Service Level------------------------------------------
[0.         2.89007492 2.98726995 0.         2.99985301 2.85644907]
---------------------

------------------------------Total Service Level------------------------------------------
[0.         0.9935352  0.99403721 0.         1.         0.96216287]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 1593.415223798519, 198.0365260734938, 288.1530516679109, 149.48815461924315, 162.7489865030927]
Total On hand: 2391.8419426622595
------------------------------Total Service Level------------------------------------------
[0.         1.96169536 1.98390121 0.         1.99656861 1.93187591]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 1521.3641130447836, 191.60455425671543, 290.37448731410507, 168.41413943205237, 170.73586960319415]
Total On hand: 4734.33510631311
------------------------------Total Service Level------------------------------------------
[0.         2.95826833 2.94116473 0.         2.9953025  2.86535467]
----------------------

Summary: iters  43 evals  50 noisy_evals   0 cycles   5 opt_time   96.39 tot_time   96.39 obj      3374.105525 gap 100.00


In [106]:
print("\nFinal objective: " + "{0:10.3f}".format(val))
print("\nFinal solution: " + str(x))
print("\nTotal time: " + "{0:3.2f}".format(elapsed_time) + " minutes")


Final objective:   3374.106

Final solution: [1999.99999985  262.95471301  699.99999945  135.22575796  131.29300107
  939.93598069  176.91366542   65.67762629  139.64499702  185.91050244]

Total time: 1.61 minutes


In [107]:
final_solution=x
final_inventory_stock = final_solution[:(numNodes - 1)]
final_ROP = final_solution[(numNodes - 1):]
print('Optimized Inventory Position',np.round(final_inventory_stock)) ## [ plant_area WH1  WH2 Store1 Store2]
print('Optimized Reoorder point',np.round(final_ROP))                 ## [ plant_area WH1  WH2 Store1 Store2]

Optimized Inventory Position [2000.  263.  700.  135.  131.]
Optimized Reoorder point [940. 177.  66. 140. 186.]


### Predict rbfOpt Lost Sales Using Inputs and Optimized values

In [108]:
guess=final_solution
numVars=len(final_solution)

In [109]:
start_time = time.time()
bb = rbfopt.RbfoptUserBlackBox(numVars, np.array([0] * numVars), np.array(guess),
                               np.array(['R'] * numVars), predict_rbfOpt_lost_sales)
alg = rbfopt.RbfoptAlgorithm(settings, bb)
val, x, itercount, evalcount, fast_evalcount = alg.optimize()
elapsed_time = (time.time() - start_time)/60.0

  Iter  Cycle  Action             Objective value      Time      Gap
  ----  -----  ------             ---------------      ----      ---
------------------------------Total Service Level------------------------------------------
[0.         0.68582285 0.22948315 0.27439256 0.1677263  0.06100072]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 347.0914713325853, 9.223615840889098, 31.472795490000376, 7.948186566032839, 0.8310899568947374]
Total On hand: 396.56715918640236
------------------------------Total Service Level------------------------------------------
[0.         1.38996971 0.42590963 0.54115145 0.33010298 0.11828022]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 300.3017136185639, 10.346300350099474, 32.72795779120614, 9.284386503374607, 0.8415592851818381]
Total On hand: 750.0690767348283
------------------------------Total Service L

------------------------------Total Service Level------------------------------------------
[0.         0.76877433 0.29797082 0.44111651 0.11577204 0.21219816]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 426.9204057549537, 17.119497619723276, 102.81741181246576, 1.5613540275460775, 13.86597616334636]
Total On hand: 562.2846453780352
------------------------------Total Service Level------------------------------------------
[0.         1.55489181 0.63396713 0.85824634 0.22199393 0.43229071]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 419.38237308584655, 27.146661865784825, 97.8586347311619, 2.447998326764339, 14.531525223305916]
Total On hand: 1123.6518386108987
------------------------------Total Service Level------------------------------------------
[0.         2.35055542 0.94488152 1.27860636 0.32434307 0.67288865]
----------------------

------------------------------Total Service Level------------------------------------------
[0.         2.9783995  1.22039504 0.17728349 0.03124141 0.03583948]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 512.3523090267392, 42.63607404416407, 0.2822811681834672, 1.2411769406436877, 0.8560434447829475]
Total On hand: 1660.7569964593613
------------------------------Total Service Level------------------------------------------
[0.         3.9576295  1.64690402 0.23536541 0.04165055 0.04762389]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 491.56886108546473, 38.23741299892347, 0.19152334165685836, 0.8785950532751015, 1.6076762782855323]
Total On hand: 2193.241065216967
------------------------------Total Service Level------------------------------------------
[0.         4.94479557 2.07227785 0.29279599 0.05208704 0.05877863]
-------------------

------------------------------Total Service Level------------------------------------------
[0.         2.03510906 0.90278519 0.58996969 0.76753751 0.30476157]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 524.2768992882616, 21.76066718745318, 17.44240031658752, 9.938903857180785, 1.0433042402594086]
Total On hand: 1711.1791425320434
------------------------------Total Service Level------------------------------------------
[0.         2.71077591 1.20786563 0.78981059 1.01730971 0.41614021]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 493.3476566974103, 21.030134042304507, 12.38701648202629, 9.584288175294938, 2.4163833436050934]
Total On hand: 2249.9446212726843
------------------------------Total Service Level------------------------------------------
[0.         3.3812445  1.50779751 0.98322452 1.27974866 0.51898834]
-----------------------

------------------------------Total Service Level------------------------------------------
[0.         4.65309113 2.25783366 1.62977288 1.0056973  2.30331801]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 574.7946302375221, 40.10420681908621, 35.16507767827219, 7.236296125708939, 40.7420286746967]
Total On hand: 4188.937917248011
------------------------------Total Service Level------------------------------------------
[0.         5.42284927 2.64802383 1.898235   1.17871727 2.67883154]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 546.4873654508847, 40.28722560000661, 38.91879959992853, 5.970431712467667, 39.27779902481053]
Total On hand: 4859.879538636109
------------------------------Total Service Level------------------------------------------
[0.         6.24318118 3.01428788 2.14529727 1.32505335 3.09734401]
-----------------------------

...

------------------------------Total Service Level------------------------------------------
[0.         0.95335834 0.59391926 0.3797374  0.3774612  0.49712623]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 899.8474187381292, 54.55789140731378, 83.75815803827166, 27.937457092858878, 65.58566799247527]
Total On hand: 1131.686593269049
------------------------------Total Service Level------------------------------------------
[0.         1.90824613 1.23956485 0.77388984 0.75318298 0.97311875]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 934.7257959135659, 55.81380148887746, 85.19815629177614, 29.523182570504378, 58.65197354075415]
Total On hand: 2295.599503074527
------------------------------Total Service Level------------------------------------------
[0.         2.85136943 1.85345384 1.17024648 1.09200239 1.41657072]
--------------------------

------------------------------Total Service Level------------------------------------------
[0.         0.84136311 0.49259693 0.35361519 0.39030155 0.49292042]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 1038.5204006859224, 32.8292741473298, 80.2803440284916, 25.996664241421847, 64.03489238851782]
Total On hand: 1241.6615754916834
------------------------------Total Service Level------------------------------------------
[0.         1.74048937 1.00675642 0.69312789 0.83450075 1.01838847]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 1012.6675829092345, 40.460845457037536, 75.26586266612809, 35.6051999480469, 79.66253907965128]
Total On hand: 2485.323605551782
------------------------------Total Service Level------------------------------------------
[0.         2.68261481 1.50649686 1.05768014 1.23240544 1.51921717]
--------------------------

Service level penalty: [0.         0.0604405  0.45345098 0.         0.55332553 0.42601969]
Objective Function value: 1494572.472605132
    40      5  AdjLocalStep        1494572.472605    116.28   100.01  
------------------------------Total Service Level------------------------------------------
[0.         0.88182306 0.49498423 0.35787694 0.41257971 0.49889383]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 1073.4910004870183, 37.771360350902825, 89.70303099343633, 29.869718471463678, 86.861023275791]
Total On hand: 1317.6961335786123
------------------------------Total Service Level------------------------------------------
[0.         1.77662914 0.98912885 0.70302315 0.82591032 1.07761486]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 1123.0019329952388, 36.80704954566006, 86.03720753068212, 29.51501297452508, 86.87800786783626]
Total On han

    41      5  RefinementStep      1477637.545833    117.59   100.01  
------------------------------Total Service Level------------------------------------------
[0.         0.92866935 0.48420865 0.37330423 0.41163304 0.48037862]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 1134.5113941839595, 34.72403758425188, 73.68586958224499, 25.002951057202935, 65.65373037017028]
Total On hand: 1333.5779827778294
------------------------------Total Service Level------------------------------------------
[0.         1.86322609 0.98088111 0.76929972 0.83410886 1.00794652]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 1146.0081903993926, 36.937126012722565, 86.54498028327924, 29.350791802908756, 75.70473929567491]
Total On hand: 2708.1238105718076
------------------------------Total Service Level------------------------------------------
[0.         2.7864

Summary: iters  43 evals  50 noisy_evals   0 cycles   5 opt_time  118.90 tot_time  118.90 obj   1367177.573162 gap 100.01


In [110]:
print("\nFinal objective: " + "{0:10.3f}".format(val))
print("\nFinal solution: " + str(x))
print("\nTotal time: " + "{0:3.2f}".format(elapsed_time) + " minutes")


Final objective: 1367177.573

Final solution: [2.00000000e+03 5.87234925e-08 6.99999999e+02 4.84665547e+01
 1.31293001e+02 9.39935981e+02 1.76913665e+02 6.56776263e+01
 1.39644997e+02 1.85910502e+02]

Total time: 1.98 minutes


In [111]:
final_solution=x
final_inventory_stock = final_solution[:(numNodes - 1)]
final_ROP = final_solution[(numNodes - 1):]
print('Optimized Inventory Position',np.round(final_inventory_stock)) ## [ plant_area WH1  WH2 Store1 Store2]
print('Optimized Reoorder point',np.round(final_ROP))                 ## [ plant_area WH1  WH2 Store1 Store2]

Optimized Inventory Position [2000.    0.  700.   48.  131.]
Optimized Reoorder point [940. 177.  66. 140. 186.]


### rbfOpt Black-Box Back Order Optimization

In [112]:
start_time = time.time()
bb = rbfopt.RbfoptUserBlackBox(numVars, np.array([0] * numVars), np.array(guess),
                               np.array(['R'] * numVars), getObj_rbfOpt_lost_sales)
alg = rbfopt.RbfoptAlgorithm(settings, bb)
val, x, itercount, evalcount, fast_evalcount = alg.optimize()
elapsed_time = (time.time() - start_time)/60.0

  Iter  Cycle  Action             Objective value      Time      Gap
  ----  -----  ------             ---------------      ----      ---
------------------------------Total Service Level------------------------------------------
[0.         0.80581192 0.50915218 0.         0.71617377 0.27887341]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 482.59727854865406, 25.95078684147201, 139.26696976586067, 43.35668483416032, 6.2108325739947405]
Total On hand: 697.3825525641417
------------------------------Total Service Level------------------------------------------
[0.         1.60588957 0.98885657 0.         1.3471053  0.54535035]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 475.19641864225355, 25.12812803700347, 152.5638599409519, 37.10233585351692, 6.381579293354108]
Total On hand: 1393.7548743312218
------------------------------Total Service L

------------------------------Total Service Level------------------------------------------
[0.         2.74096541 2.58955511 0.         1.70482578 2.16114734]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 665.0329739457871, 101.47563421752731, 249.97569639022706, 14.345135148781921, 56.80432822698791]
Total On hand: 3206.751135265799
------------------------------Total Service Level------------------------------------------
[0.         3.6972257  3.47861281 0.         2.28086016 2.84371704]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 638.6125325131995, 104.82602054574717, 224.23131223561694, 13.298391631622781, 56.78026223629534]
Total On hand: 4244.49965442828
------------------------------Total Service Level------------------------------------------
[0.         4.59932304 4.32144698 0.         2.80932934 3.56839776]
-----------------------

------------------------------Total Service Level------------------------------------------
[0.         2.98551932 2.33792838 0.         0.1346844  0.0800505 ]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 564.1734203952706, 92.95369186655698, 26.577041082048748, 5.086268039925767, 3.3964176250904146]
Total On hand: 2104.943635398691
------------------------------Total Service Level------------------------------------------
[0.         3.97269296 3.16856094 0.         0.18032009 0.10548341]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 564.1673850454926, 89.4591328283123, 26.72891001968647, 2.7393199161518176, 3.8391659986322875]
Total On hand: 2791.8775492069667
------------------------------Total Service Level------------------------------------------
[0.         4.95758874 3.95975714 0.         0.22476852 0.13341983]
------------------------

------------------------------Total Service Level------------------------------------------
[0.         3.11729692 3.04947818 0.         3.68230762 1.7362181 ]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 606.8629899665224, 58.91931455717252, 84.61927463570053, 65.36250270586224, 11.054739340980154]
Total On hand: 3478.9294201363887
------------------------------Total Service Level------------------------------------------
[0.         3.89252487 3.80188595 0.         4.64592271 2.21452301]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 698.4787546584013, 66.2683699266871, 90.3914922323839, 67.30625160388406, 13.088565302309553]
Total On hand: 4414.462853860055
------------------------------Total Service Level------------------------------------------
[0.         4.62476212 4.55064098 0.         5.57156609 2.63033162]
---------------------------

------------------------------Total Service Level------------------------------------------
[0.         5.31931395 4.01759323 0.         4.96591967 5.05964172]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 846.2537548084383, 76.98774059199708, 158.53927263777553, 44.70709079874549, 118.80525399589978]
Total On hand: 7449.23868930939
------------------------------Total Service Level------------------------------------------
[0.         6.22152037 4.65957417 0.         5.85114562 5.91954587]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 893.9261853790732, 76.80090186548598, 166.2854795646553, 49.026347586311196, 113.1438571031475]
Total On hand: 8748.421460808064
------------------------------Total Service Level------------------------------------------
[0.         7.10921572 5.3477499  0.         6.67205622 6.70401625]
--------------------------

...

------------------------------Total Service Level------------------------------------------
[0.         0.99138005 0.96819236 0.         1.         0.92034755]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 1543.2893437777134, 158.4827647222801, 213.49207051638982, 126.3150584087338, 116.0604780491053]
Total On hand: 2157.639715474222
------------------------------Total Service Level------------------------------------------
[0.         1.9629568  1.93442942 0.         1.99999999 1.86514057]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 1389.3717036294936, 144.03613047129528, 198.04353886447643, 124.46439224175313, 112.3783525953403]
Total On hand: 4125.933833276581
------------------------------Total Service Level------------------------------------------
[0.         2.9336773  2.88687351 0.         2.99999999 2.77770034]
----------------------

------------------------------Total Service Level------------------------------------------
[0.         0.97840705 0.96137373 0.         0.99533344 0.88468437]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 1493.9422158373377, 151.29058848043, 176.99621252715542, 124.46908123186276, 109.75830449274814]
Total On hand: 2056.456402569534
------------------------------Total Service Level------------------------------------------
[0.         1.94872347 1.91914302 0.         1.99533343 1.78936806]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 1476.109269613308, 135.5301813640563, 183.70380685904905, 125.43194396655656, 113.82247528459231]
Total On hand: 4091.0540796570963
------------------------------Total Service Level------------------------------------------
[0.         2.9335328  2.90907405 0.         2.99533343 2.72773216]
----------------------

------------------------------Total Service Level------------------------------------------
[0.         0.9894941  0.9672427  0.         1.         0.95542979]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 1527.0199736996726, 153.21934448500022, 202.80741184815423, 124.24532290609908, 111.7423842806922]
Total On hand: 2119.034437219618
------------------------------Total Service Level------------------------------------------
[0.         1.96464142 1.93432566 0.         1.99999999 1.92208354]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 1402.3100564916847, 163.51237116693397, 192.69590302675243, 120.47141353153408, 116.12184106442734]
Total On hand: 4114.1460225009505
------------------------------Total Service Level------------------------------------------
[0.         2.93877605 2.89036681 0.         2.99492859 2.89814604]
------------------

------------------------------Total Service Level------------------------------------------
[0.         0.98944359 0.96798783 0.         1.         0.95538528]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 1526.9208122008315, 154.04773666332653, 202.86932535777373, 124.29240001339468, 111.71482332439696]
Total On hand: 2119.8450975597234
------------------------------Total Service Level------------------------------------------
[0.         1.97149281 1.94677381 0.         1.99999999 1.89090366]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 1450.6399200154747, 157.42344664343716, 200.81012979622633, 122.80488837375911, 112.75087934645268]
Total On hand: 4164.274361735073
------------------------------Total Service Level------------------------------------------
[0.         2.93919345 2.894497   0.         2.99621264 2.83022059]
-----------------

Summary: iters  43 evals  50 noisy_evals   0 cycles   5 opt_time  113.10 tot_time  113.10 obj     11234.506081 gap 100.00


In [113]:
print("\nFinal objective: " + "{0:10.3f}".format(val))
print("\nFinal solution: " + str(x))
print("\nTotal time: " + "{0:3.2f}".format(elapsed_time) + " minutes")


Final objective:  11234.506

Final solution: [1.83711224e+03 1.58609357e+02 5.96480124e+02 3.66443259e+01
 1.68442369e-08 9.39935981e+02 1.76913665e+02 6.32010644e+01
 1.39644997e+02 1.85910502e+02]

Total time: 1.89 minutes


In [114]:
final_solution=x
final_inventory_stock = final_solution[:(numNodes - 1)]
final_ROP = final_solution[(numNodes - 1):]
print('Optimized Inventory Position',np.round(final_inventory_stock)) ## [ plant_area WH1  WH2 Store1 Store2]
print('Optimized Reoorder point',np.round(final_ROP))                 ## [ plant_area WH1  WH2 Store1 Store2]

Optimized Inventory Position [1837.  159.  596.   37.    0.]
Optimized Reoorder point [940. 177.  63. 140. 186.]


### Predict rbfOpt Back Order Using Inputs and Optimized values

In [115]:
guess=final_solution
numVars=len(final_solution)

In [116]:
start_time = time.time()
bb = rbfopt.RbfoptUserBlackBox(numVars, np.array([0] * numVars), np.array(guess),
                               np.array(['R'] * numVars), predict_rbfOpt_back_order)
alg = rbfopt.RbfoptAlgorithm(settings, bb)
val, x, itercount, evalcount, fast_evalcount = alg.optimize()
elapsed_time = (time.time() - start_time)/60.0

  Iter  Cycle  Action             Objective value      Time      Gap
  ----  -----  ------             ---------------      ----      ---
------------------------------Total Service Level------------------------------------------
[1.         0.63396237 0.10036867 0.08308003 0.05596723 0.01041795]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 191.75199971596376, 0.34435782468557957, 2.9280529109138373, 0.14329992522059895, 0.009507745683131067]
Total On hand: 195.17721812246688
------------------------------Total Service Level------------------------------------------
[2.         1.2595773  0.1850435  0.1678503  0.10631389 0.02058811]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 203.48261539156817, 0.24713560246335733, 2.804686169467769, 0.21772766560867618, 0.009507745683131067]
Total On hand: 401.938890697258
------------------------------Tot

------------------------------Total Service Level------------------------------------------
[2.         1.504713   0.24274606 0.25006458 0.11691397 0.31914262]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 290.09008236015194, 0.8082143909366079, 5.526872897201353, 0.0837944017876072, 0.5558587511085576]
Total On hand: 595.7793161571158
------------------------------Total Service Level------------------------------------------
[3.         2.26563289 0.37689167 0.35870663 0.17148322 0.48229407]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 321.9910879540916, 1.628505466375828, 5.070116961032545, 0.16527209425171055, 0.21861958370285256]
Total On hand: 924.8529182165703
------------------------------Total Service Level------------------------------------------
[4.         2.97319308 0.49252467 0.50183107 0.23097129 0.64108552]
--------------------

------------------------------Total Service Level------------------------------------------
[2.         1.96361979 0.2601326  0.09253303 0.01036801 0.01755325]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 480.41882667603363, 1.41517299890959, 0.058725385703145665, 0.3198078241495141, 0.8679959617524086]
Total On hand: 941.4324282484106
------------------------------Total Service Level------------------------------------------
[3.         2.94834105 0.3822139  0.14397672 0.01560731 0.02620828]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 471.9507506725131, 1.01517299890959, 0.058725385703145665, 0.3198078241495141, 0.706552526869862]
Total On hand: 1415.483437656556
------------------------------Total Service Level------------------------------------------
[4.         3.91038073 0.52081885 0.19122172 0.02074757 0.03520162]
--------------------

------------------------------Total Service Level------------------------------------------
[4.         2.39825099 0.46222442 0.18279198 0.58235253 0.36685874]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 369.55099819061934, 1.0811769389921537, 1.9195791216581484, 0.35313651301655286, 0.2026339131417288]
Total On hand: 1483.498595128582
------------------------------Total Service Level------------------------------------------
[5.         3.0197727  0.57446303 0.22879616 0.72163661 0.46002565]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 373.45796252599513, 0.9304971067492785, 1.4132717936774424, 0.4685936584137182, 0.23033975860148206]
Total On hand: 1859.9992599720192
------------------------------Total Service Level------------------------------------------
[6.         3.64324548 0.68263344 0.28169894 0.89445977 0.56745587]
---------------

------------------------------Total Service Level------------------------------------------
[6.         4.32617513 0.71871216 0.61606276 0.56564957 0.9255716 ]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 384.23644659559915, 0.6005004826469241, 3.917021592840274, 0.328492247485451, 0.7327094408886747]
Total On hand: 2390.7690329420184
------------------------------Total Service Level------------------------------------------
[7.         4.97895541 0.82626576 0.70678758 0.64773297 1.07963668]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 400.35236967334964, 0.667667631960515, 4.860373989879017, 0.4288494823392876, 1.1528718471108255]
Total On hand: 2798.2311655666576
------------------------------Total Service Level------------------------------------------
[8.         5.70787195 0.92448733 0.80293584 0.72811625 1.22845932]
--------------------

...

------------------------------Total Service Level------------------------------------------
[16.         14.57936706  3.49483081  1.94719994  3.02611988  3.04740612]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 894.7969937692126, 0.598162236101276, 3.8537871440287077, 0.5183385310022307, 0.3460025810703953]
Total On hand: 14308.768542690406
------------------------------Total Service Level------------------------------------------
[17.         15.52272409  3.74904444  2.07357807  3.22300619  3.21948097]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 966.6873166669501, 0.5163674166601099, 4.209342699584263, 0.418707168816302, 0.3538165355284117]
Total On hand: 15280.954093177945
------------------------------Total Service Level------------------------------------------
[18.         16.44592476  3.96614433  2.19407982  3.4210333   3.40774305]
---

------------------------------Total Service Level------------------------------------------
[16.         14.55935403  1.99868656  1.94052231  1.89399452  3.0233882 ]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 900.190334599856, 0.9026074639991474, 3.559850648201714, 0.340966353581178, 0.549674338220346]
Total On hand: 14165.974241099599
------------------------------Total Service Level------------------------------------------
[17.         15.47634579  2.11828919  2.05546965  2.04064827  3.18858242]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 910.4865333161633, 1.2673087362948754, 3.6794749164413463, 0.717584767737867, 0.7314559517749634]
Total On hand: 15082.85659878801
------------------------------Total Service Level------------------------------------------
[18.         16.45801972  2.24231517  2.18533614  2.14170278  3.38146404]
------

------------------------------Total Service Level------------------------------------------
[1.60000000e+01 1.60000000e+01 2.00155309e+00 8.87467044e-09
 1.20982756e-01 2.13394529e-01]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 1011.4598584306392, 1.40159028127129, 1.2711401431484324e-12, 1.0349831646278813, 1.0266590584522952]
Total On hand: 16202.067451018185
------------------------------Total Service Level------------------------------------------
[1.70000000e+01 1.70000000e+01 2.13575426e+00 9.38489531e-09
 1.28812806e-01 2.26073127e-01]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 968.7072747650475, 1.3543680590490677, 1.2711401431484324e-12, 0.7505429290264666, 2.6348767157458943]
Total On hand: 17175.514513487055
------------------------------Total Service Level------------------------------------------
[1.80000000e+01 1.80000000e+0

------------------------------Total Service Level------------------------------------------
[16.         13.30298884  3.34044819  1.86528059  1.8514451   2.82028911]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 785.4840975388888, 0.9160034199481006, 6.279282485839506, 0.2840199609182293, 0.5739459391481139]
Total On hand: 12087.879773420209
------------------------------Total Service Level------------------------------------------
[17.         14.13006802  3.55581912  1.99326604  1.95689712  3.02415924]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 736.1926481644398, 0.8687811977258785, 3.743540035440799, 0.37846440536267373, 0.3883618584629458]
Total On hand: 12829.45156908164
------------------------------Total Service Level------------------------------------------
[18.         14.97285013  3.77930977  2.10159452  2.07540058  3.21892069]
--

------------------------------Total Service Level------------------------------------------
[18.         16.46169716  3.8491082   1.9259631   3.07056414  3.22551622]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 916.7965151228254, 0.5354699483577717, 3.8343400839519153, 0.3912020635477531, 0.42438671980156584]
Total On hand: 16821.71395765434
------------------------------Total Service Level------------------------------------------
[19.         17.3917819   4.08277271  2.03310775  3.24584761  3.40379294]
------------------------------Total Average on Hand------------------------------------------
Per Node On hand: [0.0, 940.574897463924, 0.9014954522710991, 4.714240395910118, 0.6576364286549631, 0.8987734396031317]
Total On hand: 17769.461000834704
------------------------------Total Service Level------------------------------------------
[20.         18.3038895   4.3016062   2.13482564  3.45268698  3.57477334]
--

In [117]:
print("\nFinal objective: " + "{0:10.3f}".format(val))
print("\nFinal solution: " + str(x))
print("\nTotal time: " + "{0:3.2f}".format(elapsed_time) + " minutes")


Final objective: 2270569.981

Final solution: [1.83711224e+03 1.41431458e-07 4.92136829e+02 1.37117653e-08
 1.02527958e-08 9.39935980e+02 1.50268504e+02 4.77904283e+01
 1.17642476e+02 1.10926301e+02]

Total time: 1.95 minutes


In [118]:
final_solution=x
final_inventory_stock = final_solution[:(numNodes - 1)]
final_ROP = final_solution[(numNodes - 1):]
print('Optimized Inventory Position',np.round(final_inventory_stock)) ## [ plant_area WH1  WH2 Store1 Store2]
print('Optimized Reoorder point',np.round(final_ROP))                 ## [ plant_area WH1  WH2 Store1 Store2]

Optimized Inventory Position [1837.    0.  492.    0.    0.]
Optimized Reoorder point [940. 150.  48. 118. 111.]


### Insights

Lost Sales
Optimized Inventory Position [2000.  263.  700.  135.  131.]
Optimized Reoorder point [940. 177.  66. 140. 186.]

## Final Thoughts

### The policy learnt is still not optimal 
since it considers the state of each node wrt to the overall network and not the overall network itself.
Use RL learnt policy to include overall state of the network

### Using the Initial inventory guess and initial reorder points as input
### Demand can either be historical data that can be randomly chosen as is shown in example
   or it could be more cyclic that is in every tcycle as per number of steps you choose a cross section
   from data that is equal to number of time steps, thsi way the demand behaviour & Seasonality is captured.

### Lead time can also be sourced in the same way from historical data randmomly or as per number of steps you choose a cross section
   from data that is equal to number of time steps, thsi way the demand behaviour & Seasonality is captured.
    
### Once you have the optimal solution you could use that as an initial parameter and 
   input FUTURE DEMAND FORECAST & LEAD TIME as inputs into the equation and run the simulation to equal the numberr of time steps.
   NOTE: Number of Steps and DEMAND FORECAST and LEAD TIME Should equal in SHAPE
    
### Although Lead time is used as control parameter it is just to intriduce variability. In reality it is not tracking
   that the shipment shoukd reach to requestor in LTD days. For this we shoudl use RL based learning to find optimal policy
        